In [1]:
import numpy as np
import pandas as pd
import copy

import torch
from torch.utils.data import TensorDataset, DataLoader
from sklearn.preprocessing import MinMaxScaler

from data import fetch_dataset
from util import move_sliding_window, num_params
from model import LSTMModel
from algorithm import fedcsakd, fedavg

pd.set_option('display.max_columns', None)
pd.set_option('display.max_columns', None)
np.set_printoptions(suppress=True, floatmode='fixed')

In [2]:
if torch.cuda.is_available():
    device = torch.device("cuda")
    print('running on gpu')
else:
    device = torch.device("cpu")

running on gpu


# Parameters

In [3]:
window_size = 90 # Define window_size period and split inputs/labels\
batch_size = 1024
label_col_index = 0

# seq_len = 90  # (timestamps)
hidden_dim = 50
n_layers = 2
lr = 0.0001
output_dim = 1

#fed train params
num_local_epochs = 1
max_rounds = 100 #nb of total rounds for training


# Data Preperation

In [4]:
dataframes = fetch_dataset("./heterog")

Floor0
Floor1
Floor10
Floor11
Floor12
Floor13
Floor14
Floor15
Floor16
Floor17
Floor18
Floor19
Floor2
Floor20
Floor21
Floor22
Floor23
Floor24
Floor25
Floor26
Floor27
Floor28
Floor29
Floor3
Floor30
Floor31
Floor32
Floor33
Floor34
Floor35
Floor36
Floor37
Floor38
Floor39
Floor4
Floor40
Floor41
Floor42
Floor43
Floor44
Floor45
Floor46
Floor47
Floor48
Floor49
Floor5
Floor50
Floor51
Floor52
Floor53
Floor54
Floor55
Floor56
Floor57
Floor58
Floor59
Floor6
Floor60
Floor61
Floor62
Floor63
Floor64
Floor65
Floor66
Floor67
Floor68
Floor69
Floor7
Floor70
Floor71
Floor72
Floor73
Floor74
Floor75
Floor76
Floor77
Floor78
Floor79
Floor8
Floor80
Floor81
Floor82
Floor83
Floor84
Floor85
Floor86
Floor87
Floor88
Floor89
Floor9


In [5]:
# n_clients = len(dataframes) #total number of clients to partition data into

In [6]:
for _, df in dataframes.items():
    print(df.columns)
    print(df.shape)
    input_dim=df.shape[1]

Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
      dtype='object')
(68183, 9)
Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
      dtype='object')
(58618, 9)
Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
      dtype='object')
(46840, 9)
Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
      dtype='object')
(65390, 9)
Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
      dtype='object')
(57176, 9)
Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
      dtype='object')
(51707, 9)
Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
      dtype='object')
(47453, 9)
Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
 

# LSTM model

In [7]:
lstm = LSTMModel(input_dim, hidden_dim, output_dim, n_layers)
model_type = 'LSTM'
print(lstm)
print(num_params(lstm))

LSTMModel(
  (lstm): LSTM(9, 50, num_layers=2, batch_first=True)
  (fc): Linear(in_features=50, out_features=1, bias=True)
  (tanh): Tanh()
)
32651


# Build the training set

## FedCSA

## 10

In [8]:
n_clients=10

In [9]:
train_loader = []
test_loader = []
label_scalers = []
i=0
for _, df in dataframes.items():
    if i==n_clients:
        break
    inputs_cols_indices = range(0, df.shape[1])  # use (total_demand,Year,Month,Day,Hour,Minute) columns as features
    #move the window
    inputs, labels = move_sliding_window(
        df.values,
        window_size,
        inputs_cols_indices=inputs_cols_indices,
        label_col_index=label_col_index
    )

    # Normalize the input data columns
    sc = MinMaxScaler()
    # Obtaining the scaler for the labels(usage data) so that output can be re-scaled to actual value during evaluation
    label_sc = MinMaxScaler()

    # Split data into train/test portions and combining all data into a single array
    test_portion = int(0.2 * len(inputs))

    train_x = sc.fit_transform(inputs[:-test_portion].reshape(-1, window_size * df.shape[1]))
    train_x = train_x.reshape(-1, window_size, df.shape[1])
    train_y = label_sc.fit_transform(labels[:-test_portion])

    test_x = sc.transform(inputs[-test_portion:].reshape(-1, window_size * df.shape[1]))
    test_x = test_x.reshape(-1, window_size, df.shape[1])
    test_y = label_sc.transform(labels[-test_portion:])

    # test_x.append(testx)
    # test_y.append(testy)
    label_scalers.append(label_sc)

    # pytorch data loaders
    train_data = TensorDataset(torch.from_numpy(train_x).to('cpu'), torch.from_numpy(train_y).to('cpu'))
    train_loader.append(DataLoader(train_data, batch_size=batch_size, drop_last=True))# Drop the last incomplete batch
    test_data = TensorDataset(torch.from_numpy(test_x).to('cpu'), torch.from_numpy(test_y).to('cpu'))
    test_loader.append(DataLoader(test_data, batch_size=batch_size))# Drop the last incomplete batch

    # release some memory
    del train_x, train_y
    i=i+1

(68093, 90, 9) (68093, 1)
(58528, 90, 9) (58528, 1)
(46750, 90, 9) (46750, 1)
(65300, 90, 9) (65300, 1)
(57086, 90, 9) (57086, 1)
(51617, 90, 9) (51617, 1)
(47363, 90, 9) (47363, 1)
(68901, 90, 9) (68901, 1)
(67168, 90, 9) (67168, 1)
(69578, 90, 9) (69578, 1)


In [10]:
%%time
lstm_csakd = copy.deepcopy(lstm)
outputs_csakd1, targets_csakd1, loss_csakd1, smape_csakd1, mae_csakd1, rmse_csakd1,global_model, aggregated_logits = fedavg(
    global_model = lstm_csakd,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = 1,
    model_type = model_type,
    device = device,
)
outputs_csakd, targets_csakd, loss_csakd, smape_csakd, mae_csakd, rmse_csakd = fedcsakd(
    global_model = global_model,
    aggregated_logits=aggregated_logits,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds-1,
    model_type = model_type,
    device = device,
)


starting avg round 0
clients:  [0 1 2 3 4 5 6 7 8 9]
round 0, starting client 1/10, id: 0
Epoch [1/1], Train Loss: 0.15514601134466674
round 0, starting client 2/10, id: 1
Epoch [1/1], Train Loss: 0.14287791947523754
round 0, starting client 3/10, id: 2
Epoch [1/1], Train Loss: 0.12616322686274847
round 0, starting client 4/10, id: 3
Epoch [1/1], Train Loss: 0.12589487754831127
round 0, starting client 5/10, id: 4
Epoch [1/1], Train Loss: 0.14941424537788736
round 0, starting client 6/10, id: 5
Epoch [1/1], Train Loss: 0.1362801698036492
round 0, starting client 7/10, id: 6
Epoch [1/1], Train Loss: 0.16154998480468186
round 0, starting client 8/10, id: 7
Epoch [1/1], Train Loss: 0.13826576170493968
round 0, starting client 9/10, id: 8
Epoch [1/1], Train Loss: 0.13452585815237114
round 0, starting client 10/10, id: 9
Epoch [1/1], Train Loss: 0.1235271968913299
calc smape: 99.99999987650997%
MAE: 17.41751711085417
RMSE: 26.267091484953923
Average Loss:  0.10704103162835452

starting rou

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.08764865389972365
loss error: 0.0361
round 1, starting client 2/10, id: 1
Epoch [1/1], Train Loss: 0.0771030637125174
loss error: 0.0318
round 1, starting client 3/10, id: 2
Epoch [1/1], Train Loss: 0.06717959594809345
loss error: 0.0583
round 1, starting client 4/10, id: 3
Epoch [1/1], Train Loss: 0.0684007043566774
loss error: 0.0290
round 1, starting client 5/10, id: 4
Epoch [1/1], Train Loss: 0.08232128941877322
loss error: 0.0504
round 1, starting client 6/10, id: 5
Epoch [1/1], Train Loss: 0.07479702779091896
loss error: 0.0675
round 1, starting client 7/10, id: 6
Epoch [1/1], Train Loss: 0.09273790004285608
loss error: 0.0424
round 1, starting client 8/10, id: 7
Epoch [1/1], Train Loss: 0.07182998182076326
loss error: 0.0358
round 1, starting client 9/10, id: 8
Epoch [1/1], Train Loss: 0.07430321966799407
loss error: 0.0679
round 1, starting client 10/10, id: 9
Epoch [1/1], Train Loss: 0.06345821348562215
loss error: 0.0337
calc smape: 52.9625297752387

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0453133010569046
loss error: 0.0296
round 2, starting client 2/10, id: 1
Epoch [1/1], Train Loss: 0.036577941974004095
loss error: 0.0422
round 2, starting client 3/10, id: 2
Epoch [1/1], Train Loss: 0.033600480037017
loss error: 0.0296
round 2, starting client 4/10, id: 3
Epoch [1/1], Train Loss: 0.03769348538024169
loss error: 0.0267
round 2, starting client 5/10, id: 4
Epoch [1/1], Train Loss: 0.03960622427985071
loss error: 0.0411
round 2, starting client 6/10, id: 5
Epoch [1/1], Train Loss: 0.03656236543320119
loss error: 0.0424
round 2, starting client 7/10, id: 6
Epoch [1/1], Train Loss: 0.043557498906109784
loss error: 0.0477
round 2, starting client 8/10, id: 7
Epoch [1/1], Train Loss: 0.033466655831291985
loss error: 0.0277
round 2, starting client 9/10, id: 8
Epoch [1/1], Train Loss: 0.04043525052615083
loss error: 0.0213
round 2, starting client 10/10, id: 9
Epoch [1/1], Train Loss: 0.031114005690647498
loss error: 0.0478
calc smape: 57.2040969518

...

Epoch [1/1], Train Loss: 0.0016769439175303251
loss error: 0.0591
round 96, starting client 2/7, id: 1
Epoch [1/1], Train Loss: 0.0017863272443517215
loss error: 0.0401
round 96, starting client 3/7, id: 5
Epoch [1/1], Train Loss: 0.00201396665458257
loss error: 0.0361
round 96, starting client 4/7, id: 6
Epoch [1/1], Train Loss: 0.002151879274249807
loss error: 0.0688
round 96, starting client 5/7, id: 7
Epoch [1/1], Train Loss: 0.0019268393093212085
loss error: 0.0502
round 96, starting client 6/7, id: 8
Epoch [1/1], Train Loss: 0.0018906222299847287
loss error: 0.0569
round 96, starting client 7/7, id: 9
Epoch [1/1], Train Loss: 0.0017910285670360603
loss error: 0.0461
calc smape: 19.292220321116254%
MAE: 1.5506305824862299
RMSE: 3.5344058998467784
Average Loss:  0.0020601436927694234
tmp_cl [0, 1, 2, 4, 6], n_tmp_cl 5
tmp_cl_cid [0, 1, 5, 7, 9]
{0: 0, 1: 0, 5: 0, 6: 4, 7: 0, 8: 2, 9: 0}
Updated clients:  [0, 1, 5, 6, 7, 8, 9]

starting round 97
clients:  [0, 1, 5, 6, 7, 8, 9]
round

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0016694127500742535
loss error: 0.0682
round 97, starting client 2/7, id: 1
Epoch [1/1], Train Loss: 0.0017883104776653153
loss error: 0.0591
round 97, starting client 3/7, id: 5
Epoch [1/1], Train Loss: 0.0020116441228310573
loss error: 0.0662
round 97, starting client 4/7, id: 6
Epoch [1/1], Train Loss: 0.0021453310756067577
loss error: 0.0639
round 97, starting client 5/7, id: 7
Epoch [1/1], Train Loss: 0.001923669511928562
loss error: 0.0353
round 97, starting client 6/7, id: 8
Epoch [1/1], Train Loss: 0.00188167312880978
loss error: 0.0362
round 97, starting client 7/7, id: 9
Epoch [1/1], Train Loss: 0.0017844440157500077
loss error: 0.0559
calc smape: 20.881113440087095%
MAE: 1.905459616547854
RMSE: 4.331227571784157
Average Loss:  0.00226663431796479
tmp_cl [0, 1, 4, 5, 6], n_tmp_cl 5
tmp_cl_cid [0, 1, 7, 8, 9]
{0: 0, 1: 0, 5: 1, 6: 5, 7: 0, 8: 0, 9: 0}
Updated clients:  [0, 1, 5, 6, 7, 8, 9]

starting round 98
clients:  [0, 1, 5, 6, 7, 8, 9]
round 98,

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0016617070002709784
loss error: 0.0248
round 98, starting client 2/7, id: 1
Epoch [1/1], Train Loss: 0.001769040141435754
loss error: 0.0500
round 98, starting client 3/7, id: 5
Epoch [1/1], Train Loss: 0.0020110263220784767
loss error: 0.0607
round 98, starting client 4/7, id: 6
Epoch [1/1], Train Loss: 0.0021378535802439587
loss error: 0.0621
round 98, starting client 5/7, id: 7
Epoch [1/1], Train Loss: 0.0019183231819294053
loss error: 0.1034
round 98, starting client 6/7, id: 8
Epoch [1/1], Train Loss: 0.001872995579469716
loss error: 0.0542
round 98, starting client 7/7, id: 9
Epoch [1/1], Train Loss: 0.0017782649484689576
loss error: 0.0606
calc smape: 20.72289786788614%
MAE: 1.8216929234618002
RMSE: 4.213266234488306
Average Loss:  0.002083446284402906
tmp_cl [0, 1], n_tmp_cl 2
tmp_cl_cid [0, 1]
{0: 0, 1: 0, 5: 2, 6: 6, 7: 1, 8: 1, 9: 1}
Updated clients:  [0, 1, 5, 6, 7, 8, 9]
CPU times: total: 1h 22min 6s
Wall time: 1h 23min 54s


In [11]:
loss_csakd = np.insert(loss_csakd, 0, loss_csakd1)
smape_csakd = np.insert(smape_csakd, 0, smape_csakd1)
mae_csakd = np.insert(mae_csakd, 0, mae_csakd1)
rmse_csakd = np.insert(mae_csakd, 0, mae_csakd1)

In [12]:
np.save(f'metrics/fedcsakd_outputs_C{n_clients}.npy', np.array(outputs_csakd, dtype=object))
np.save(f'metrics/fedcsakd_targets_C{n_clients}.npy', np.array(targets_csakd, dtype=object))
np.save(f'metrics/fedcsakd_loss_C{n_clients}.npy', loss_csakd)
np.save(f'metrics/fedcsakd_smape_C{n_clients}.npy', smape_csakd)
np.save(f'metrics/fedcsakd_mae_C{n_clients}.npy', mae_csakd)
np.save(f'metrics/fedcsakd_rmse_C{n_clients}.npy', rmse_csakd)

## 20

In [13]:
n_clients=20

In [14]:
train_loader = []
test_loader = []
label_scalers = []
i=0
for _, df in dataframes.items():
    if i==n_clients:
        break
    inputs_cols_indices = range(0, df.shape[1])  # use (total_demand,Year,Month,Day,Hour,Minute) columns as features
    #move the window
    inputs, labels = move_sliding_window(
        df.values,
        window_size,
        inputs_cols_indices=inputs_cols_indices,
        label_col_index=label_col_index
    )

    # Normalize the input data columns
    sc = MinMaxScaler()
    # Obtaining the scaler for the labels(usage data) so that output can be re-scaled to actual value during evaluation
    label_sc = MinMaxScaler()

    # Split data into train/test portions and combining all data into a single array
    test_portion = int(0.2 * len(inputs))

    train_x = sc.fit_transform(inputs[:-test_portion].reshape(-1, window_size * df.shape[1]))
    train_x = train_x.reshape(-1, window_size, df.shape[1])
    train_y = label_sc.fit_transform(labels[:-test_portion])

    test_x = sc.transform(inputs[-test_portion:].reshape(-1, window_size * df.shape[1]))
    test_x = test_x.reshape(-1, window_size, df.shape[1])
    test_y = label_sc.transform(labels[-test_portion:])

    # test_x.append(testx)
    # test_y.append(testy)
    label_scalers.append(label_sc)

    # pytorch data loaders
    train_data = TensorDataset(torch.from_numpy(train_x).to('cpu'), torch.from_numpy(train_y).to('cpu'))
    train_loader.append(DataLoader(train_data, batch_size=batch_size, drop_last=True))# Drop the last incomplete batch
    test_data = TensorDataset(torch.from_numpy(test_x).to('cpu'), torch.from_numpy(test_y).to('cpu'))
    test_loader.append(DataLoader(test_data, batch_size=batch_size))# Drop the last incomplete batch

    # release some memory
    del train_x, train_y
    i=i+1

(68093, 90, 9) (68093, 1)
(58528, 90, 9) (58528, 1)
(46750, 90, 9) (46750, 1)
(65300, 90, 9) (65300, 1)
(57086, 90, 9) (57086, 1)
(51617, 90, 9) (51617, 1)
(47363, 90, 9) (47363, 1)
(68901, 90, 9) (68901, 1)
(67168, 90, 9) (67168, 1)
(69578, 90, 9) (69578, 1)
(62003, 90, 9) (62003, 1)
(49050, 90, 9) (49050, 1)
(61853, 90, 9) (61853, 1)
(69521, 90, 9) (69521, 1)
(67302, 90, 9) (67302, 1)
(72217, 90, 9) (72217, 1)
(46055, 90, 9) (46055, 1)
(57157, 90, 9) (57157, 1)
(64807, 90, 9) (64807, 1)
(66845, 90, 9) (66845, 1)


In [15]:
%%time
lstm_csakd = copy.deepcopy(lstm)
outputs_csakd1, targets_csakd1, loss_csakd1, smape_csakd1, mae_csakd1, rmse_csakd1,global_model, aggregated_logits = fedavg(
    global_model = lstm_csakd,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = 1,
    model_type = model_type,
    device = device,
)
outputs_csakd, targets_csakd, loss_csakd, smape_csakd, mae_csakd, rmse_csakd = fedcsakd(
    global_model = global_model,
    aggregated_logits=aggregated_logits,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds-1,
    model_type = model_type,
    device = device,
)


starting avg round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19]
round 0, starting client 1/20, id: 0
Epoch [1/1], Train Loss: 0.15514601134466674
round 0, starting client 2/20, id: 1
Epoch [1/1], Train Loss: 0.14287791947523754
round 0, starting client 3/20, id: 2
Epoch [1/1], Train Loss: 0.12616322686274847
round 0, starting client 4/20, id: 3
Epoch [1/1], Train Loss: 0.12589487754831127
round 0, starting client 5/20, id: 4
Epoch [1/1], Train Loss: 0.14941424537788736
round 0, starting client 6/20, id: 5
Epoch [1/1], Train Loss: 0.1362801698036492
round 0, starting client 7/20, id: 6
Epoch [1/1], Train Loss: 0.16154998480468186
round 0, starting client 8/20, id: 7
Epoch [1/1], Train Loss: 0.13826576170493968
round 0, starting client 9/20, id: 8
Epoch [1/1], Train Loss: 0.13452585815237114
round 0, starting client 10/20, id: 9
Epoch [1/1], Train Loss: 0.1235271968913299
round 0, starting client 11/20, id: 10
Epoch [1/1], Train Loss: 0.15574187909563383
rou

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.08707354013931079
loss error: 0.0681
round 1, starting client 2/20, id: 1
Epoch [1/1], Train Loss: 0.07653493728074759
loss error: 0.0435
round 1, starting client 3/20, id: 2
Epoch [1/1], Train Loss: 0.06669540015152758
loss error: 0.0303
round 1, starting client 4/20, id: 3
Epoch [1/1], Train Loss: 0.06793755194281831
loss error: 0.0388
round 1, starting client 5/20, id: 4
Epoch [1/1], Train Loss: 0.08174255007708615
loss error: 0.0336
round 1, starting client 6/20, id: 5
Epoch [1/1], Train Loss: 0.0742754625622183
loss error: 0.0818
round 1, starting client 7/20, id: 6
Epoch [1/1], Train Loss: 0.0921271509314711
loss error: 0.0327
round 1, starting client 8/20, id: 7
Epoch [1/1], Train Loss: 0.07125860691632863
loss error: 0.0307
round 1, starting client 9/20, id: 8
Epoch [1/1], Train Loss: 0.07382728843591536
loss error: 0.0284
round 1, starting client 10/20, id: 9
Epoch [1/1], Train Loss: 0.06297221334642489
loss error: 0.0585
round 1, starting client 11/

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.04494075810993618
loss error: 0.0321
round 2, starting client 2/20, id: 1
Epoch [1/1], Train Loss: 0.03628745888256365
loss error: 0.0495
round 2, starting client 3/20, id: 2
Epoch [1/1], Train Loss: 0.0334411020287209
loss error: 0.0454
round 2, starting client 4/20, id: 3
Epoch [1/1], Train Loss: 0.03747763544978465
loss error: 0.0513
round 2, starting client 5/20, id: 4
Epoch [1/1], Train Loss: 0.039303735491227024
loss error: 0.0653
round 2, starting client 6/20, id: 5
Epoch [1/1], Train Loss: 0.03631153248716145
loss error: 0.0334
round 2, starting client 7/20, id: 6
Epoch [1/1], Train Loss: 0.04317639828533739
loss error: 0.0332
round 2, starting client 8/20, id: 7
Epoch [1/1], Train Loss: 0.03315531799815736
loss error: 0.0386
round 2, starting client 9/20, id: 8
Epoch [1/1], Train Loss: 0.040213964986973084
loss error: 0.0322
round 2, starting client 10/20, id: 9
Epoch [1/1], Train Loss: 0.030840613913756833
loss error: 0.0602
round 2, starting client

...

Epoch [1/1], Train Loss: 0.001714991374305924
loss error: 0.0479
round 96, starting client 2/19, id: 1
Epoch [1/1], Train Loss: 0.0018383887350662714
loss error: 0.0317
round 96, starting client 3/19, id: 2
Epoch [1/1], Train Loss: 0.0020645887270802636
loss error: 0.0555
round 96, starting client 4/19, id: 3
Epoch [1/1], Train Loss: 0.0022363105729477956
loss error: 0.0370
round 96, starting client 5/19, id: 4
Epoch [1/1], Train Loss: 0.0019787912963445046
loss error: 0.0285
round 96, starting client 6/19, id: 5
Epoch [1/1], Train Loss: 0.0019234511666581964
loss error: 0.0865
round 96, starting client 7/19, id: 6
Epoch [1/1], Train Loss: 0.0018360345070627892
loss error: 0.0614
round 96, starting client 8/19, id: 7
Epoch [1/1], Train Loss: 0.0014262721876016344
loss error: 0.0266
round 96, starting client 9/19, id: 8
Epoch [1/1], Train Loss: 0.002440189852047927
loss error: 0.0671
round 96, starting client 10/19, id: 9
Epoch [1/1], Train Loss: 0.00182290977574195
loss error: 0.0433
r

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0017080328411879547
loss error: 0.0573
round 97, starting client 2/19, id: 1
Epoch [1/1], Train Loss: 0.0018177425158986207
loss error: 0.0530
round 97, starting client 3/19, id: 2
Epoch [1/1], Train Loss: 0.0020590667069579163
loss error: 0.0594
round 97, starting client 4/19, id: 3
Epoch [1/1], Train Loss: 0.0022258579231086463
loss error: 0.0375
round 97, starting client 5/19, id: 4
Epoch [1/1], Train Loss: 0.0019729120196478275
loss error: 0.0405
round 97, starting client 6/19, id: 5
Epoch [1/1], Train Loss: 0.0019145828962791713
loss error: 0.0488
round 97, starting client 7/19, id: 6
Epoch [1/1], Train Loss: 0.001828577586550366
loss error: 0.0395
round 97, starting client 8/19, id: 7
Epoch [1/1], Train Loss: 0.001421792554572435
loss error: 0.0318
round 97, starting client 9/19, id: 8
Epoch [1/1], Train Loss: 0.0024301148436139696
loss error: 0.0433
round 97, starting client 10/19, id: 9
Epoch [1/1], Train Loss: 0.0018154551114464446
loss error: 0.0346

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0017017128038272823
loss error: 0.0426
round 98, starting client 2/19, id: 1
Epoch [1/1], Train Loss: 0.0018190881327932906
loss error: 0.0301
round 98, starting client 3/19, id: 2
Epoch [1/1], Train Loss: 0.0020512152324146074
loss error: 0.0250
round 98, starting client 4/19, id: 3
Epoch [1/1], Train Loss: 0.002218851026412392
loss error: 0.0298
round 98, starting client 5/19, id: 4
Epoch [1/1], Train Loss: 0.001959492153466933
loss error: 0.0439
round 98, starting client 6/19, id: 5
Epoch [1/1], Train Loss: 0.0019080777310591659
loss error: 0.0398
round 98, starting client 7/19, id: 6
Epoch [1/1], Train Loss: 0.001820179614918055
loss error: 0.0611
round 98, starting client 8/19, id: 7
Epoch [1/1], Train Loss: 0.0014197824869902349
loss error: 0.0351
round 98, starting client 9/19, id: 8
Epoch [1/1], Train Loss: 0.0024151278014939567
loss error: 0.0765
round 98, starting client 10/19, id: 9
Epoch [1/1], Train Loss: 0.0018083102040691303
loss error: 0.0346


In [16]:
loss_csakd = np.insert(loss_csakd, 0, loss_csakd1)
smape_csakd = np.insert(smape_csakd, 0, smape_csakd1)
mae_csakd = np.insert(mae_csakd, 0, mae_csakd1)
rmse_csakd = np.insert(mae_csakd, 0, mae_csakd1)

In [17]:
np.save(f'metrics/fedcsakd_outputs_C{n_clients}.npy', np.array(outputs_csakd, dtype=object))
np.save(f'metrics/fedcsakd_targets_C{n_clients}.npy', np.array(targets_csakd, dtype=object))
np.save(f'metrics/fedcsakd_loss_C{n_clients}.npy', loss_csakd)
np.save(f'metrics/fedcsakd_smape_C{n_clients}.npy', smape_csakd)
np.save(f'metrics/fedcsakd_mae_C{n_clients}.npy', mae_csakd)
np.save(f'metrics/fedcsakd_rmse_C{n_clients}.npy', rmse_csakd)

## 30

In [18]:
n_clients=30

In [19]:
train_loader = []
test_loader = []
label_scalers = []
i=0
for _, df in dataframes.items():
    if i==n_clients:
        break
    inputs_cols_indices = range(0, df.shape[1])  # use (total_demand,Year,Month,Day,Hour,Minute) columns as features
    #move the window
    inputs, labels = move_sliding_window(
        df.values,
        window_size,
        inputs_cols_indices=inputs_cols_indices,
        label_col_index=label_col_index
    )

    # Normalize the input data columns
    sc = MinMaxScaler()
    # Obtaining the scaler for the labels(usage data) so that output can be re-scaled to actual value during evaluation
    label_sc = MinMaxScaler()

    # Split data into train/test portions and combining all data into a single array
    test_portion = int(0.2 * len(inputs))

    train_x = sc.fit_transform(inputs[:-test_portion].reshape(-1, window_size * df.shape[1]))
    train_x = train_x.reshape(-1, window_size, df.shape[1])
    train_y = label_sc.fit_transform(labels[:-test_portion])

    test_x = sc.transform(inputs[-test_portion:].reshape(-1, window_size * df.shape[1]))
    test_x = test_x.reshape(-1, window_size, df.shape[1])
    test_y = label_sc.transform(labels[-test_portion:])

    # test_x.append(testx)
    # test_y.append(testy)
    label_scalers.append(label_sc)

    # pytorch data loaders
    train_data = TensorDataset(torch.from_numpy(train_x).to('cpu'), torch.from_numpy(train_y).to('cpu'))
    train_loader.append(DataLoader(train_data, batch_size=batch_size, drop_last=True))# Drop the last incomplete batch
    test_data = TensorDataset(torch.from_numpy(test_x).to('cpu'), torch.from_numpy(test_y).to('cpu'))
    test_loader.append(DataLoader(test_data, batch_size=batch_size))# Drop the last incomplete batch

    # release some memory
    del train_x, train_y
    i=i+1

(68093, 90, 9) (68093, 1)
(58528, 90, 9) (58528, 1)
(46750, 90, 9) (46750, 1)
(65300, 90, 9) (65300, 1)
(57086, 90, 9) (57086, 1)
(51617, 90, 9) (51617, 1)
(47363, 90, 9) (47363, 1)
(68901, 90, 9) (68901, 1)
(67168, 90, 9) (67168, 1)
(69578, 90, 9) (69578, 1)
(62003, 90, 9) (62003, 1)
(49050, 90, 9) (49050, 1)
(61853, 90, 9) (61853, 1)
(69521, 90, 9) (69521, 1)
(67302, 90, 9) (67302, 1)
(72217, 90, 9) (72217, 1)
(46055, 90, 9) (46055, 1)
(57157, 90, 9) (57157, 1)
(64807, 90, 9) (64807, 1)
(66845, 90, 9) (66845, 1)
(61800, 90, 9) (61800, 1)
(55024, 90, 9) (55024, 1)
(65910, 90, 9) (65910, 1)
(49996, 90, 9) (49996, 1)
(63049, 90, 9) (63049, 1)
(64836, 90, 9) (64836, 1)
(64007, 90, 9) (64007, 1)
(69858, 90, 9) (69858, 1)
(56491, 90, 9) (56491, 1)
(65359, 90, 9) (65359, 1)


In [20]:
%%time
lstm_csakd = copy.deepcopy(lstm)
outputs_csakd1, targets_csakd1, loss_csakd1, smape_csakd1, mae_csakd1, rmse_csakd1,global_model, aggregated_logits = fedavg(
    global_model = lstm_csakd,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = 1,
    model_type = model_type,
    device = device,
)
outputs_csakd, targets_csakd, loss_csakd, smape_csakd, mae_csakd, rmse_csakd = fedcsakd(
    global_model = global_model,
    aggregated_logits=aggregated_logits,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds-1,
    model_type = model_type,
    device = device,
)


starting avg round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29]
round 0, starting client 1/30, id: 0
Epoch [1/1], Train Loss: 0.15514601134466674
round 0, starting client 2/30, id: 1
Epoch [1/1], Train Loss: 0.14287791947523754
round 0, starting client 3/30, id: 2
Epoch [1/1], Train Loss: 0.12616322686274847
round 0, starting client 4/30, id: 3
Epoch [1/1], Train Loss: 0.12589487754831127
round 0, starting client 5/30, id: 4
Epoch [1/1], Train Loss: 0.14941424537788736
round 0, starting client 6/30, id: 5
Epoch [1/1], Train Loss: 0.1362801698036492
round 0, starting client 7/30, id: 6
Epoch [1/1], Train Loss: 0.16154998480468186
round 0, starting client 8/30, id: 7
Epoch [1/1], Train Loss: 0.13826576170493968
round 0, starting client 9/30, id: 8
Epoch [1/1], Train Loss: 0.13452585815237114
round 0, starting client 10/30, id: 9
Epoch [1/1], Train Loss: 0.1235271968913299
round 0, starting client 11/30, id: 10
Epoch [1/1], Trai

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.08705578501916156
loss error: 0.0437
round 1, starting client 2/30, id: 1
Epoch [1/1], Train Loss: 0.07650693833000133
loss error: 0.0335
round 1, starting client 3/30, id: 2
Epoch [1/1], Train Loss: 0.06666412473552756
loss error: 0.0348
round 1, starting client 4/30, id: 3
Epoch [1/1], Train Loss: 0.06790867699858022
loss error: 0.0553
round 1, starting client 5/30, id: 4
Epoch [1/1], Train Loss: 0.08171761916442351
loss error: 0.0439
round 1, starting client 6/30, id: 5
Epoch [1/1], Train Loss: 0.07423727102577687
loss error: 0.0432
round 1, starting client 7/30, id: 6
Epoch [1/1], Train Loss: 0.09207663654878334
loss error: 0.0350
round 1, starting client 8/30, id: 7
Epoch [1/1], Train Loss: 0.07124195167056796
loss error: 0.0323
round 1, starting client 9/30, id: 8
Epoch [1/1], Train Loss: 0.07379459156296575
loss error: 0.0507
round 1, starting client 10/30, id: 9
Epoch [1/1], Train Loss: 0.06297133774582848
loss error: 0.0339
round 1, starting client 1

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.045260143659587165
loss error: 0.0499
round 2, starting client 2/30, id: 1
Epoch [1/1], Train Loss: 0.036575274821370844
loss error: 0.0436
round 2, starting client 3/30, id: 2
Epoch [1/1], Train Loss: 0.03369251969787809
loss error: 0.0373
round 2, starting client 4/30, id: 3
Epoch [1/1], Train Loss: 0.037723433043734704
loss error: 0.0468
round 2, starting client 5/30, id: 4
Epoch [1/1], Train Loss: 0.039595905860716644
loss error: 0.0418
round 2, starting client 6/30, id: 5
Epoch [1/1], Train Loss: 0.03658453586976974
loss error: 0.0295
round 2, starting client 7/30, id: 6
Epoch [1/1], Train Loss: 0.04347970417222461
loss error: 0.0685
round 2, starting client 8/30, id: 7
Epoch [1/1], Train Loss: 0.033456124119319995
loss error: 0.0347
round 2, starting client 9/30, id: 8
Epoch [1/1], Train Loss: 0.04044758940402132
loss error: 0.0373
round 2, starting client 10/30, id: 9
Epoch [1/1], Train Loss: 0.03111858917745176
loss error: 0.0273
round 2, starting cli

...

Epoch [1/1], Train Loss: 0.0019244883497210466
loss error: 0.0493
round 96, starting client 2/22, id: 1
Epoch [1/1], Train Loss: 0.0020447966869040907
loss error: 0.0318
round 96, starting client 3/22, id: 2
Epoch [1/1], Train Loss: 0.002314247918548062
loss error: 0.0337
round 96, starting client 4/22, id: 3
Epoch [1/1], Train Loss: 0.0024740318151410014
loss error: 0.0518
round 96, starting client 5/22, id: 4
Epoch [1/1], Train Loss: 0.0021676624627699225
loss error: 0.0368
round 96, starting client 6/22, id: 5
Epoch [1/1], Train Loss: 0.0021226373944955414
loss error: 0.0620
round 96, starting client 7/22, id: 6
Epoch [1/1], Train Loss: 0.002029801468755043
loss error: 0.0388
round 96, starting client 8/22, id: 7
Epoch [1/1], Train Loss: 0.0015550510488881045
loss error: 0.0257
round 96, starting client 9/22, id: 8
Epoch [1/1], Train Loss: 0.002708981960985022
loss error: 0.0833
round 96, starting client 10/22, id: 9
Epoch [1/1], Train Loss: 0.002016209919357034
loss error: 0.0461
r

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0019173808220141336
loss error: 0.0351
round 97, starting client 2/22, id: 1
Epoch [1/1], Train Loss: 0.002039162409103786
loss error: 0.0277
round 97, starting client 3/22, id: 2
Epoch [1/1], Train Loss: 0.002310751869420831
loss error: 0.0410
round 97, starting client 4/22, id: 3
Epoch [1/1], Train Loss: 0.0024659714396750815
loss error: 0.0629
round 97, starting client 5/22, id: 4
Epoch [1/1], Train Loss: 0.00215948680786162
loss error: 0.0482
round 97, starting client 6/22, id: 5
Epoch [1/1], Train Loss: 0.0021155465678020847
loss error: 0.0431
round 97, starting client 7/22, id: 6
Epoch [1/1], Train Loss: 0.00202095099863269
loss error: 0.0451
round 97, starting client 8/22, id: 7
Epoch [1/1], Train Loss: 0.0015512004171779276
loss error: 0.0441
round 97, starting client 9/22, id: 8
Epoch [1/1], Train Loss: 0.0026983026842712066
loss error: 0.0460
round 97, starting client 10/22, id: 9
Epoch [1/1], Train Loss: 0.0020103056934506944
loss error: 0.0392
rou

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0019099347678865394
loss error: 0.0555
round 98, starting client 2/22, id: 1
Epoch [1/1], Train Loss: 0.0020325419894005685
loss error: 0.0580
round 98, starting client 3/22, id: 2
Epoch [1/1], Train Loss: 0.0023054483996626605
loss error: 0.0353
round 98, starting client 4/22, id: 3
Epoch [1/1], Train Loss: 0.002458204887350838
loss error: 0.0344
round 98, starting client 5/22, id: 4
Epoch [1/1], Train Loss: 0.0021519119367109274
loss error: 0.0318
round 98, starting client 6/22, id: 5
Epoch [1/1], Train Loss: 0.00210899311787216
loss error: 0.0383
round 98, starting client 7/22, id: 6
Epoch [1/1], Train Loss: 0.0020137301605270314
loss error: 0.0889
round 98, starting client 8/22, id: 7
Epoch [1/1], Train Loss: 0.0015472999388431107
loss error: 0.0569
round 98, starting client 9/22, id: 8
Epoch [1/1], Train Loss: 0.0026877265347418585
loss error: 0.0590
round 98, starting client 10/22, id: 9
Epoch [1/1], Train Loss: 0.0020042642976881727
loss error: 0.0260


In [21]:
loss_csakd = np.insert(loss_csakd, 0, loss_csakd1)
smape_csakd = np.insert(smape_csakd, 0, smape_csakd1)
mae_csakd = np.insert(mae_csakd, 0, mae_csakd1)
rmse_csakd = np.insert(mae_csakd, 0, mae_csakd1)

In [22]:
np.save(f'metrics/fedcsakd_outputs_C{n_clients}.npy', np.array(outputs_csakd, dtype=object))
np.save(f'metrics/fedcsakd_targets_C{n_clients}.npy', np.array(targets_csakd, dtype=object))
np.save(f'metrics/fedcsakd_loss_C{n_clients}.npy', loss_csakd)
np.save(f'metrics/fedcsakd_smape_C{n_clients}.npy', smape_csakd)
np.save(f'metrics/fedcsakd_mae_C{n_clients}.npy', mae_csakd)
np.save(f'metrics/fedcsakd_rmse_C{n_clients}.npy', rmse_csakd)

## 40

In [8]:
n_clients=40

In [9]:
train_loader = []
test_loader = []
label_scalers = []
i=0
for _, df in dataframes.items():
    if i==n_clients:
        break
    inputs_cols_indices = range(0, df.shape[1])  # use (total_demand,Year,Month,Day,Hour,Minute) columns as features
    #move the window
    inputs, labels = move_sliding_window(
        df.values,
        window_size,
        inputs_cols_indices=inputs_cols_indices,
        label_col_index=label_col_index
    )

    # Normalize the input data columns
    sc = MinMaxScaler()
    # Obtaining the scaler for the labels(usage data) so that output can be re-scaled to actual value during evaluation
    label_sc = MinMaxScaler()

    # Split data into train/test portions and combining all data into a single array
    test_portion = int(0.2 * len(inputs))

    train_x = sc.fit_transform(inputs[:-test_portion].reshape(-1, window_size * df.shape[1]))
    train_x = train_x.reshape(-1, window_size, df.shape[1])
    train_y = label_sc.fit_transform(labels[:-test_portion])

    test_x = sc.transform(inputs[-test_portion:].reshape(-1, window_size * df.shape[1]))
    test_x = test_x.reshape(-1, window_size, df.shape[1])
    test_y = label_sc.transform(labels[-test_portion:])

    # test_x.append(testx)
    # test_y.append(testy)
    label_scalers.append(label_sc)

    # pytorch data loaders
    train_data = TensorDataset(torch.from_numpy(train_x).to('cpu'), torch.from_numpy(train_y).to('cpu'))
    train_loader.append(DataLoader(train_data, batch_size=batch_size, drop_last=True))# Drop the last incomplete batch
    test_data = TensorDataset(torch.from_numpy(test_x).to('cpu'), torch.from_numpy(test_y).to('cpu'))
    test_loader.append(DataLoader(test_data, batch_size=batch_size))# Drop the last incomplete batch

    # release some memory
    del train_x, train_y
    i=i+1

(68093, 90, 9) (68093, 1)
(58528, 90, 9) (58528, 1)
(46750, 90, 9) (46750, 1)
(65300, 90, 9) (65300, 1)
(57086, 90, 9) (57086, 1)
(51617, 90, 9) (51617, 1)
(47363, 90, 9) (47363, 1)
(68901, 90, 9) (68901, 1)
(67168, 90, 9) (67168, 1)
(69578, 90, 9) (69578, 1)
(62003, 90, 9) (62003, 1)
(49050, 90, 9) (49050, 1)
(61853, 90, 9) (61853, 1)
(69521, 90, 9) (69521, 1)
(67302, 90, 9) (67302, 1)
(72217, 90, 9) (72217, 1)
(46055, 90, 9) (46055, 1)
(57157, 90, 9) (57157, 1)
(64807, 90, 9) (64807, 1)
(66845, 90, 9) (66845, 1)
(61800, 90, 9) (61800, 1)
(55024, 90, 9) (55024, 1)
(65910, 90, 9) (65910, 1)
(49996, 90, 9) (49996, 1)
(63049, 90, 9) (63049, 1)
(64836, 90, 9) (64836, 1)
(64007, 90, 9) (64007, 1)
(69858, 90, 9) (69858, 1)
(56491, 90, 9) (56491, 1)
(65359, 90, 9) (65359, 1)
(61733, 90, 9) (61733, 1)
(66320, 90, 9) (66320, 1)
(61236, 90, 9) (61236, 1)
(71305, 90, 9) (71305, 1)
(52888, 90, 9) (52888, 1)
(58160, 90, 9) (58160, 1)
(70972, 90, 9) (70972, 1)
(61987, 90, 9) (61987, 1)
(43972, 90, 

In [10]:
%%time
lstm_csakd = copy.deepcopy(lstm)
outputs_csakd1, targets_csakd1, loss_csakd1, smape_csakd1, mae_csakd1, rmse_csakd1,global_model, aggregated_logits = fedavg(
    global_model = lstm_csakd,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = 1,
    model_type = model_type,
    device = device,
)
outputs_csakd, targets_csakd, loss_csakd, smape_csakd, mae_csakd, rmse_csakd = fedcsakd(
    global_model = global_model,
    aggregated_logits=aggregated_logits,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds-1,
    model_type = model_type,
    device = device,
)


starting avg round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39]
round 0, starting client 1/40, id: 0
Epoch [1/1], Train Loss: 0.054271208860401834
round 0, starting client 2/40, id: 1
Epoch [1/1], Train Loss: 0.04577829299701585
round 0, starting client 3/40, id: 2
Epoch [1/1], Train Loss: 0.04103380545145935
round 0, starting client 4/40, id: 3
Epoch [1/1], Train Loss: 0.046200293098010256
round 0, starting client 5/40, id: 4
Epoch [1/1], Train Loss: 0.04912142671475355
round 0, starting client 6/40, id: 5
Epoch [1/1], Train Loss: 0.045274433074519026
round 0, starting client 7/40, id: 6
Epoch [1/1], Train Loss: 0.05243948630585864
round 0, starting client 8/40, id: 7
Epoch [1/1], Train Loss: 0.042509005211715425
round 0, starting client 9/40, id: 8
Epoch [1/1], Train Loss: 0.04878560238732741
round 0, starting client 10/40, id: 9
Epoch [1/1], Train Loss: 0.03991996903938276
round 0, starting cl

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.04698182920099428
loss error: 0.0452
round 1, starting client 2/40, id: 1
Epoch [1/1], Train Loss: 0.03988751508295538
loss error: 0.0220
round 1, starting client 3/40, id: 2
Epoch [1/1], Train Loss: 0.03687767260190514
loss error: 0.0643
round 1, starting client 4/40, id: 3
Epoch [1/1], Train Loss: 0.040831911541959816
loss error: 0.0458
round 1, starting client 5/40, id: 4
Epoch [1/1], Train Loss: 0.042755604044280276
loss error: 0.0363
round 1, starting client 6/40, id: 5
Epoch [1/1], Train Loss: 0.03987192376516759
loss error: 0.0514
round 1, starting client 7/40, id: 6
Epoch [1/1], Train Loss: 0.045721157730833906
loss error: 0.0471
round 1, starting client 8/40, id: 7
Epoch [1/1], Train Loss: 0.036773556667678765
loss error: 0.0279
round 1, starting client 9/40, id: 8
Epoch [1/1], Train Loss: 0.04285066248849036
loss error: 0.0380
round 1, starting client 10/40, id: 9
Epoch [1/1], Train Loss: 0.03445757252888546
loss error: 0.0293
round 1, starting clie

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.035510642524316634
loss error: 0.0532
round 2, starting client 2/40, id: 1
Epoch [1/1], Train Loss: 0.03060305217901866
loss error: 0.0416
round 2, starting client 3/40, id: 2
Epoch [1/1], Train Loss: 0.030189532295076385
loss error: 0.0400
round 2, starting client 4/40, id: 3
Epoch [1/1], Train Loss: 0.03213858924002624
loss error: 0.0340
round 2, starting client 5/40, id: 4
Epoch [1/1], Train Loss: 0.03287062717770989
loss error: 0.0450
round 2, starting client 6/40, id: 5
Epoch [1/1], Train Loss: 0.031303512095473704
loss error: 0.0517
round 2, starting client 7/40, id: 6
Epoch [1/1], Train Loss: 0.03519234438804356
loss error: 0.0290
round 2, starting client 8/40, id: 7
Epoch [1/1], Train Loss: 0.02761755047260591
loss error: 0.0539
round 2, starting client 9/40, id: 8
Epoch [1/1], Train Loss: 0.033614822555906504
loss error: 0.0406
round 2, starting client 10/40, id: 9
Epoch [1/1], Train Loss: 0.02587609886433239
loss error: 0.0421
round 2, starting clie

...

Epoch [1/1], Train Loss: 0.001951647221708214
loss error: 0.0553
round 96, starting client 2/31, id: 1
Epoch [1/1], Train Loss: 0.002053925579336161
loss error: 0.0484
round 96, starting client 3/31, id: 2
Epoch [1/1], Train Loss: 0.0023304018791855522
loss error: 0.0534
round 96, starting client 4/31, id: 3
Epoch [1/1], Train Loss: 0.0024280156928808516
loss error: 0.0373
round 96, starting client 5/31, id: 4
Epoch [1/1], Train Loss: 0.002199594453982585
loss error: 0.0773
round 96, starting client 6/31, id: 5
Epoch [1/1], Train Loss: 0.0021669529087375854
loss error: 0.0356
round 96, starting client 7/31, id: 6
Epoch [1/1], Train Loss: 0.0020554600978849105
loss error: 0.0449
round 96, starting client 8/31, id: 7
Epoch [1/1], Train Loss: 0.0015654063921966507
loss error: 0.0704
round 96, starting client 9/31, id: 8
Epoch [1/1], Train Loss: 0.002748215477018116
loss error: 0.0403
round 96, starting client 10/31, id: 9
Epoch [1/1], Train Loss: 0.002031952958161667
loss error: 0.0399
ro

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0019435226996341404
loss error: 0.0363
round 97, starting client 2/31, id: 1
Epoch [1/1], Train Loss: 0.002044934955968832
loss error: 0.0253
round 97, starting client 3/31, id: 2
Epoch [1/1], Train Loss: 0.0023244332405738533
loss error: 0.0346
round 97, starting client 4/31, id: 3
Epoch [1/1], Train Loss: 0.002418475524595409
loss error: 0.0339
round 97, starting client 5/31, id: 4
Epoch [1/1], Train Loss: 0.0021899795471902253
loss error: 0.0425
round 97, starting client 6/31, id: 5
Epoch [1/1], Train Loss: 0.0021568560841842555
loss error: 0.0286
round 97, starting client 7/31, id: 6
Epoch [1/1], Train Loss: 0.002045866809911221
loss error: 0.0266
round 97, starting client 8/31, id: 7
Epoch [1/1], Train Loss: 0.0015606653524061914
loss error: 0.0398
round 97, starting client 9/31, id: 8
Epoch [1/1], Train Loss: 0.002736723778070882
loss error: 0.0276
round 97, starting client 10/31, id: 9
Epoch [1/1], Train Loss: 0.0020236120277938125
loss error: 0.0606
r

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0019354906179151442
loss error: 0.0328
round 98, starting client 2/31, id: 1
Epoch [1/1], Train Loss: 0.0020361378640195143
loss error: 0.0495
round 98, starting client 3/31, id: 2
Epoch [1/1], Train Loss: 0.0023183947244736674
loss error: 0.0834
round 98, starting client 4/31, id: 3
Epoch [1/1], Train Loss: 0.0024088846734158843
loss error: 0.0431
round 98, starting client 5/31, id: 4
Epoch [1/1], Train Loss: 0.002180133242456412
loss error: 0.0326
round 98, starting client 6/31, id: 5
Epoch [1/1], Train Loss: 0.002146355724835303
loss error: 0.0460
round 98, starting client 7/31, id: 6
Epoch [1/1], Train Loss: 0.0020359099537411054
loss error: 0.0450
round 98, starting client 8/31, id: 7
Epoch [1/1], Train Loss: 0.0015559805950308041
loss error: 0.0457
round 98, starting client 9/31, id: 8
Epoch [1/1], Train Loss: 0.002725225378526375
loss error: 0.1040
round 98, starting client 10/31, id: 9
Epoch [1/1], Train Loss: 0.002014976143578275
loss error: 0.0476
r

In [11]:
loss_csakd = np.insert(loss_csakd, 0, loss_csakd1)
smape_csakd = np.insert(smape_csakd, 0, smape_csakd1)
mae_csakd = np.insert(mae_csakd, 0, mae_csakd1)
rmse_csakd = np.insert(mae_csakd, 0, mae_csakd1)

In [12]:
np.save(f'metrics/fedcsakd_outputs_C{n_clients}.npy', np.array(outputs_csakd, dtype=object))
np.save(f'metrics/fedcsakd_targets_C{n_clients}.npy', np.array(targets_csakd, dtype=object))
np.save(f'metrics/fedcsakd_loss_C{n_clients}.npy', loss_csakd)
np.save(f'metrics/fedcsakd_smape_C{n_clients}.npy', smape_csakd)
np.save(f'metrics/fedcsakd_mae_C{n_clients}.npy', mae_csakd)
np.save(f'metrics/fedcsakd_rmse_C{n_clients}.npy', rmse_csakd)

## 50

In [13]:
n_clients=50

In [14]:
train_loader = []
test_loader = []
label_scalers = []
i=0
for _, df in dataframes.items():
    if i==n_clients:
        break
    inputs_cols_indices = range(0, df.shape[1])  # use (total_demand,Year,Month,Day,Hour,Minute) columns as features
    #move the window
    inputs, labels = move_sliding_window(
        df.values,
        window_size,
        inputs_cols_indices=inputs_cols_indices,
        label_col_index=label_col_index
    )

    # Normalize the input data columns
    sc = MinMaxScaler()
    # Obtaining the scaler for the labels(usage data) so that output can be re-scaled to actual value during evaluation
    label_sc = MinMaxScaler()

    # Split data into train/test portions and combining all data into a single array
    test_portion = int(0.2 * len(inputs))

    train_x = sc.fit_transform(inputs[:-test_portion].reshape(-1, window_size * df.shape[1]))
    train_x = train_x.reshape(-1, window_size, df.shape[1])
    train_y = label_sc.fit_transform(labels[:-test_portion])

    test_x = sc.transform(inputs[-test_portion:].reshape(-1, window_size * df.shape[1]))
    test_x = test_x.reshape(-1, window_size, df.shape[1])
    test_y = label_sc.transform(labels[-test_portion:])

    # test_x.append(testx)
    # test_y.append(testy)
    label_scalers.append(label_sc)

    # pytorch data loaders
    train_data = TensorDataset(torch.from_numpy(train_x).to('cpu'), torch.from_numpy(train_y).to('cpu'))
    train_loader.append(DataLoader(train_data, batch_size=batch_size, drop_last=True))# Drop the last incomplete batch
    test_data = TensorDataset(torch.from_numpy(test_x).to('cpu'), torch.from_numpy(test_y).to('cpu'))
    test_loader.append(DataLoader(test_data, batch_size=batch_size))# Drop the last incomplete batch

    # release some memory
    del train_x, train_y
    i=i+1

(68093, 90, 9) (68093, 1)
(58528, 90, 9) (58528, 1)
(46750, 90, 9) (46750, 1)
(65300, 90, 9) (65300, 1)
(57086, 90, 9) (57086, 1)
(51617, 90, 9) (51617, 1)
(47363, 90, 9) (47363, 1)
(68901, 90, 9) (68901, 1)
(67168, 90, 9) (67168, 1)
(69578, 90, 9) (69578, 1)
(62003, 90, 9) (62003, 1)
(49050, 90, 9) (49050, 1)
(61853, 90, 9) (61853, 1)
(69521, 90, 9) (69521, 1)
(67302, 90, 9) (67302, 1)
(72217, 90, 9) (72217, 1)
(46055, 90, 9) (46055, 1)
(57157, 90, 9) (57157, 1)
(64807, 90, 9) (64807, 1)
(66845, 90, 9) (66845, 1)
(61800, 90, 9) (61800, 1)
(55024, 90, 9) (55024, 1)
(65910, 90, 9) (65910, 1)
(49996, 90, 9) (49996, 1)
(63049, 90, 9) (63049, 1)
(64836, 90, 9) (64836, 1)
(64007, 90, 9) (64007, 1)
(69858, 90, 9) (69858, 1)
(56491, 90, 9) (56491, 1)
(65359, 90, 9) (65359, 1)
(61733, 90, 9) (61733, 1)
(66320, 90, 9) (66320, 1)
(61236, 90, 9) (61236, 1)
(71305, 90, 9) (71305, 1)
(52888, 90, 9) (52888, 1)
(58160, 90, 9) (58160, 1)
(70972, 90, 9) (70972, 1)
(61987, 90, 9) (61987, 1)
(43972, 90, 

In [15]:
%%time
lstm_csakd = copy.deepcopy(lstm)
outputs_csakd1, targets_csakd1, loss_csakd1, smape_csakd1, mae_csakd1, rmse_csakd1,global_model, aggregated_logits = fedavg(
    global_model = lstm_csakd,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = 1,
    model_type = model_type,
    device = device,
)
outputs_csakd, targets_csakd, loss_csakd, smape_csakd, mae_csakd, rmse_csakd = fedcsakd(
    global_model = global_model,
    aggregated_logits=aggregated_logits,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds-1,
    model_type = model_type,
    device = device,
)


starting avg round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49]
round 0, starting client 1/50, id: 0
Epoch [1/1], Train Loss: 0.054271208860401834
round 0, starting client 2/50, id: 1
Epoch [1/1], Train Loss: 0.04577829299701585
round 0, starting client 3/50, id: 2
Epoch [1/1], Train Loss: 0.04103380545145935
round 0, starting client 4/50, id: 3
Epoch [1/1], Train Loss: 0.046200293098010256
round 0, starting client 5/50, id: 4
Epoch [1/1], Train Loss: 0.04912142671475355
round 0, starting client 6/50, id: 5
Epoch [1/1], Train Loss: 0.045274433074519026
round 0, starting client 7/50, id: 6
Epoch [1/1], Train Loss: 0.05243948630585864
round 0, starting client 8/50, id: 7
Epoch [1/1], Train Loss: 0.042509005211715425
round 0, starting client 9/50, id: 8
Epoch [1/1], Train Loss: 0.04878560238732741
round 0, starting client 10/50, id: 9
Epoch [1/1], Train Loss: 0.0399199

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.04701440268248881
loss error: 0.0311
round 1, starting client 2/50, id: 1
Epoch [1/1], Train Loss: 0.03994074294136629
loss error: 0.0374
round 1, starting client 3/50, id: 2
Epoch [1/1], Train Loss: 0.03699116207038363
loss error: 0.0359
round 1, starting client 4/50, id: 3
Epoch [1/1], Train Loss: 0.04094206516210939
loss error: 0.0351
round 1, starting client 5/50, id: 4
Epoch [1/1], Train Loss: 0.042817074339836836
loss error: 0.0512
round 1, starting client 6/50, id: 5
Epoch [1/1], Train Loss: 0.039956714026629925
loss error: 0.0329
round 1, starting client 7/50, id: 6
Epoch [1/1], Train Loss: 0.0457834010390011
loss error: 0.0348
round 1, starting client 8/50, id: 7
Epoch [1/1], Train Loss: 0.036817492038573846
loss error: 0.0365
round 1, starting client 9/50, id: 8
Epoch [1/1], Train Loss: 0.04292669376501672
loss error: 0.0620
round 1, starting client 10/50, id: 9
Epoch [1/1], Train Loss: 0.034535379976862
loss error: 0.0292
round 1, starting client 1

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.03566644962806747
loss error: 0.0420
round 2, starting client 2/50, id: 1
Epoch [1/1], Train Loss: 0.030791708475185767
loss error: 0.0344
round 2, starting client 3/50, id: 2
Epoch [1/1], Train Loss: 0.0304051914718002
loss error: 0.0389
round 2, starting client 4/50, id: 3
Epoch [1/1], Train Loss: 0.0323572994447222
loss error: 0.0282
round 2, starting client 5/50, id: 4
Epoch [1/1], Train Loss: 0.03305139291015538
loss error: 0.0472
round 2, starting client 6/50, id: 5
Epoch [1/1], Train Loss: 0.031497239461168655
loss error: 0.0297
round 2, starting client 7/50, id: 6
Epoch [1/1], Train Loss: 0.035378557353003603
loss error: 0.0403
round 2, starting client 8/50, id: 7
Epoch [1/1], Train Loss: 0.027759412303566933
loss error: 0.0458
round 2, starting client 9/50, id: 8
Epoch [1/1], Train Loss: 0.03379722673875782
loss error: 0.0334
round 2, starting client 10/50, id: 9
Epoch [1/1], Train Loss: 0.026061390664566437
loss error: 0.0294
round 2, starting clien

...

Epoch [1/1], Train Loss: 0.0019510026212851957
loss error: 0.0367
round 96, starting client 2/39, id: 1
Epoch [1/1], Train Loss: 0.002045163840133075
loss error: 0.0376
round 96, starting client 3/39, id: 2
Epoch [1/1], Train Loss: 0.002324417005487096
loss error: 0.0434
round 96, starting client 4/39, id: 3
Epoch [1/1], Train Loss: 0.0024254632652645895
loss error: 0.0565
round 96, starting client 5/39, id: 4
Epoch [1/1], Train Loss: 0.002194573346059769
loss error: 0.0579
round 96, starting client 6/39, id: 5
Epoch [1/1], Train Loss: 0.002161197834357154
loss error: 0.0662
round 96, starting client 7/39, id: 6
Epoch [1/1], Train Loss: 0.0020494666579808736
loss error: 0.0315
round 96, starting client 8/39, id: 7
Epoch [1/1], Train Loss: 0.0015590110884865151
loss error: 0.0768
round 96, starting client 9/39, id: 8
Epoch [1/1], Train Loss: 0.002737103827082766
loss error: 0.0363
round 96, starting client 10/39, id: 9
Epoch [1/1], Train Loss: 0.002028739304848757
loss error: 0.0343
rou

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0019420833482828765
loss error: 0.0472
round 97, starting client 2/39, id: 1
Epoch [1/1], Train Loss: 0.0020356081762454574
loss error: 0.0418
round 97, starting client 3/39, id: 2
Epoch [1/1], Train Loss: 0.002318238252579856
loss error: 0.0310
round 97, starting client 4/39, id: 3
Epoch [1/1], Train Loss: 0.002414922059887984
loss error: 0.0458
round 97, starting client 5/39, id: 4
Epoch [1/1], Train Loss: 0.0021836267802758484
loss error: 0.0260
round 97, starting client 6/39, id: 5
Epoch [1/1], Train Loss: 0.002149627155449707
loss error: 0.0387
round 97, starting client 7/39, id: 6
Epoch [1/1], Train Loss: 0.002038968756883028
loss error: 0.1086
round 97, starting client 8/39, id: 7
Epoch [1/1], Train Loss: 0.00155366557147266
loss error: 0.0456
round 97, starting client 9/39, id: 8
Epoch [1/1], Train Loss: 0.0027252338969936743
loss error: 0.0416
round 97, starting client 10/39, id: 9
Epoch [1/1], Train Loss: 0.0020193641531578684
loss error: 0.0504
rou

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0019333825681692443
loss error: 0.0302
round 98, starting client 2/39, id: 1
Epoch [1/1], Train Loss: 0.002025783831615829
loss error: 0.0458
round 98, starting client 3/39, id: 2
Epoch [1/1], Train Loss: 0.0023107096704835482
loss error: 0.0318
round 98, starting client 4/39, id: 3
Epoch [1/1], Train Loss: 0.002404312887365984
loss error: 0.0396
round 98, starting client 5/39, id: 4
Epoch [1/1], Train Loss: 0.002173296645527113
loss error: 0.0627
round 98, starting client 6/39, id: 5
Epoch [1/1], Train Loss: 0.002138137402653229
loss error: 0.0979
round 98, starting client 7/39, id: 6
Epoch [1/1], Train Loss: 0.0020288850394757207
loss error: 0.0159
round 98, starting client 8/39, id: 7
Epoch [1/1], Train Loss: 0.0015475178776607613
loss error: 0.0682
round 98, starting client 9/39, id: 8
Epoch [1/1], Train Loss: 0.0027128027532643713
loss error: 0.0522
round 98, starting client 10/39, id: 9
Epoch [1/1], Train Loss: 0.002010204660042223
loss error: 0.0316
ro

In [16]:
loss_csakd = np.insert(loss_csakd, 0, loss_csakd1)
smape_csakd = np.insert(smape_csakd, 0, smape_csakd1)
mae_csakd = np.insert(mae_csakd, 0, mae_csakd1)
rmse_csakd = np.insert(mae_csakd, 0, mae_csakd1)

In [17]:
np.save(f'metrics/fedcsakd_outputs_C{n_clients}.npy', np.array(outputs_csakd, dtype=object))
np.save(f'metrics/fedcsakd_targets_C{n_clients}.npy', np.array(targets_csakd, dtype=object))
np.save(f'metrics/fedcsakd_loss_C{n_clients}.npy', loss_csakd)
np.save(f'metrics/fedcsakd_smape_C{n_clients}.npy', smape_csakd)
np.save(f'metrics/fedcsakd_mae_C{n_clients}.npy', mae_csakd)
np.save(f'metrics/fedcsakd_rmse_C{n_clients}.npy', rmse_csakd)

## 60

In [18]:
n_clients=60

In [19]:
train_loader = []
test_loader = []
label_scalers = []
i=0
for _, df in dataframes.items():
    if i==n_clients:
        break
    inputs_cols_indices = range(0, df.shape[1])  # use (total_demand,Year,Month,Day,Hour,Minute) columns as features
    #move the window
    inputs, labels = move_sliding_window(
        df.values,
        window_size,
        inputs_cols_indices=inputs_cols_indices,
        label_col_index=label_col_index
    )

    # Normalize the input data columns
    sc = MinMaxScaler()
    # Obtaining the scaler for the labels(usage data) so that output can be re-scaled to actual value during evaluation
    label_sc = MinMaxScaler()

    # Split data into train/test portions and combining all data into a single array
    test_portion = int(0.2 * len(inputs))

    train_x = sc.fit_transform(inputs[:-test_portion].reshape(-1, window_size * df.shape[1]))
    train_x = train_x.reshape(-1, window_size, df.shape[1])
    train_y = label_sc.fit_transform(labels[:-test_portion])

    test_x = sc.transform(inputs[-test_portion:].reshape(-1, window_size * df.shape[1]))
    test_x = test_x.reshape(-1, window_size, df.shape[1])
    test_y = label_sc.transform(labels[-test_portion:])

    # test_x.append(testx)
    # test_y.append(testy)
    label_scalers.append(label_sc)

    # pytorch data loaders
    train_data = TensorDataset(torch.from_numpy(train_x).to('cpu'), torch.from_numpy(train_y).to('cpu'))
    train_loader.append(DataLoader(train_data, batch_size=batch_size, drop_last=True))# Drop the last incomplete batch
    test_data = TensorDataset(torch.from_numpy(test_x).to('cpu'), torch.from_numpy(test_y).to('cpu'))
    test_loader.append(DataLoader(test_data, batch_size=batch_size))# Drop the last incomplete batch

    # release some memory
    del train_x, train_y
    i=i+1

(68093, 90, 9) (68093, 1)
(58528, 90, 9) (58528, 1)
(46750, 90, 9) (46750, 1)
(65300, 90, 9) (65300, 1)
(57086, 90, 9) (57086, 1)
(51617, 90, 9) (51617, 1)
(47363, 90, 9) (47363, 1)
(68901, 90, 9) (68901, 1)
(67168, 90, 9) (67168, 1)
(69578, 90, 9) (69578, 1)
(62003, 90, 9) (62003, 1)
(49050, 90, 9) (49050, 1)
(61853, 90, 9) (61853, 1)
(69521, 90, 9) (69521, 1)
(67302, 90, 9) (67302, 1)
(72217, 90, 9) (72217, 1)
(46055, 90, 9) (46055, 1)
(57157, 90, 9) (57157, 1)
(64807, 90, 9) (64807, 1)
(66845, 90, 9) (66845, 1)
(61800, 90, 9) (61800, 1)
(55024, 90, 9) (55024, 1)
(65910, 90, 9) (65910, 1)
(49996, 90, 9) (49996, 1)
(63049, 90, 9) (63049, 1)
(64836, 90, 9) (64836, 1)
(64007, 90, 9) (64007, 1)
(69858, 90, 9) (69858, 1)
(56491, 90, 9) (56491, 1)
(65359, 90, 9) (65359, 1)
(61733, 90, 9) (61733, 1)
(66320, 90, 9) (66320, 1)
(61236, 90, 9) (61236, 1)
(71305, 90, 9) (71305, 1)
(52888, 90, 9) (52888, 1)
(58160, 90, 9) (58160, 1)
(70972, 90, 9) (70972, 1)
(61987, 90, 9) (61987, 1)
(43972, 90, 

In [20]:
%%time
lstm_csakd = copy.deepcopy(lstm)
outputs_csakd1, targets_csakd1, loss_csakd1, smape_csakd1, mae_csakd1, rmse_csakd1,global_model, aggregated_logits = fedavg(
    global_model = lstm_csakd,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = 1,
    model_type = model_type,
    device = device,
)
outputs_csakd, targets_csakd, loss_csakd, smape_csakd, mae_csakd, rmse_csakd = fedcsakd(
    global_model = global_model,
    aggregated_logits=aggregated_logits,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds-1,
    model_type = model_type,
    device = device,
)


starting avg round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59]
round 0, starting client 1/60, id: 0
Epoch [1/1], Train Loss: 0.054271208860401834
round 0, starting client 2/60, id: 1
Epoch [1/1], Train Loss: 0.04577829299701585
round 0, starting client 3/60, id: 2
Epoch [1/1], Train Loss: 0.04103380545145935
round 0, starting client 4/60, id: 3
Epoch [1/1], Train Loss: 0.046200293098010256
round 0, starting client 5/60, id: 4
Epoch [1/1], Train Loss: 0.04912142671475355
round 0, starting client 6/60, id: 5
Epoch [1/1], Train Loss: 0.045274433074519026
round 0, starting client 7/60, id: 6
Epoch [1/1], Train Loss: 0.05243948630585864
round 0, starting client 8/60, id: 7
Epoch [1/1], Train Loss: 0.042509005211715425
round 0, starting client 9/60, id: 8
Epoch [1/1], Train Loss: 0.04878560238732741
round 0, starting client 10/60, id: 9
Epoc

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.04697732543045622
loss error: 0.0411
round 1, starting client 2/60, id: 1
Epoch [1/1], Train Loss: 0.03991040856473975
loss error: 0.0543
round 1, starting client 3/60, id: 2
Epoch [1/1], Train Loss: 0.03692145340351594
loss error: 0.0391
round 1, starting client 4/60, id: 3
Epoch [1/1], Train Loss: 0.04088760704240379
loss error: 0.0265
round 1, starting client 5/60, id: 4
Epoch [1/1], Train Loss: 0.04278469111093066
loss error: 0.0526
round 1, starting client 6/60, id: 5
Epoch [1/1], Train Loss: 0.03991996189579368
loss error: 0.0377
round 1, starting client 7/60, id: 6
Epoch [1/1], Train Loss: 0.04574854958903145
loss error: 0.0732
round 1, starting client 8/60, id: 7
Epoch [1/1], Train Loss: 0.036785348828108806
loss error: 0.0456
round 1, starting client 9/60, id: 8
Epoch [1/1], Train Loss: 0.042892315424978754
loss error: 0.0526
round 1, starting client 10/60, id: 9
Epoch [1/1], Train Loss: 0.0345005782459069
loss error: 0.0376
round 1, starting client 

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.03549473416411652
loss error: 0.0385
round 2, starting client 2/60, id: 1
Epoch [1/1], Train Loss: 0.030655800613264245
loss error: 0.0391
round 2, starting client 3/60, id: 2
Epoch [1/1], Train Loss: 0.030205269137190443
loss error: 0.0432
round 2, starting client 4/60, id: 3
Epoch [1/1], Train Loss: 0.03218867848901188
loss error: 0.0579
round 2, starting client 5/60, id: 4
Epoch [1/1], Train Loss: 0.03291091771627013
loss error: 0.0297
round 2, starting client 6/60, id: 5
Epoch [1/1], Train Loss: 0.03136023755650967
loss error: 0.0492
round 2, starting client 7/60, id: 6
Epoch [1/1], Train Loss: 0.035229332795417
loss error: 0.0363
round 2, starting client 8/60, id: 7
Epoch [1/1], Train Loss: 0.0276183638510839
loss error: 0.0460
round 2, starting client 9/60, id: 8
Epoch [1/1], Train Loss: 0.033662724165389166
loss error: 0.0307
round 2, starting client 10/60, id: 9
Epoch [1/1], Train Loss: 0.025932106189429763
loss error: 0.0342
round 2, starting client 

...

Epoch [1/1], Train Loss: 0.0019685836472627615
loss error: 0.0600
round 96, starting client 2/49, id: 1
Epoch [1/1], Train Loss: 0.002085635705023176
loss error: 0.0461
round 96, starting client 3/49, id: 2
Epoch [1/1], Train Loss: 0.002311156247742474
loss error: 0.0953
round 96, starting client 4/49, id: 3
Epoch [1/1], Train Loss: 0.0024576319242352804
loss error: 0.0283
round 96, starting client 5/49, id: 4
Epoch [1/1], Train Loss: 0.002236494221671654
loss error: 0.0379
round 96, starting client 6/49, id: 5
Epoch [1/1], Train Loss: 0.0022041981690563263
loss error: 0.0519
round 96, starting client 7/49, id: 6
Epoch [1/1], Train Loss: 0.002085692944584062
loss error: 0.0448
round 96, starting client 8/49, id: 7
Epoch [1/1], Train Loss: 0.0015555855451274733
loss error: 0.0571
round 96, starting client 9/49, id: 8
Epoch [1/1], Train Loss: 0.0027895115714412755
loss error: 0.0455
round 96, starting client 10/49, id: 9
Epoch [1/1], Train Loss: 0.0020598191277477543
loss error: 0.0334
r

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.00196107302326709
loss error: 0.0464
round 97, starting client 2/49, id: 1
Epoch [1/1], Train Loss: 0.002076777850743383
loss error: 0.0854
round 97, starting client 3/49, id: 2
Epoch [1/1], Train Loss: 0.0023048846794861467
loss error: 0.0332
round 97, starting client 4/49, id: 3
Epoch [1/1], Train Loss: 0.0024462696142019884
loss error: 0.0721
round 97, starting client 5/49, id: 4
Epoch [1/1], Train Loss: 0.0022254308238519693
loss error: 0.0307
round 97, starting client 6/49, id: 5
Epoch [1/1], Train Loss: 0.0021935515513177963
loss error: 0.0400
round 97, starting client 7/49, id: 6
Epoch [1/1], Train Loss: 0.0020757060139314147
loss error: 0.0488
round 97, starting client 8/49, id: 7
Epoch [1/1], Train Loss: 0.0015532560520234325
loss error: 0.0570
round 97, starting client 9/49, id: 8
Epoch [1/1], Train Loss: 0.002777035342520462
loss error: 0.0625
round 97, starting client 10/49, id: 9
Epoch [1/1], Train Loss: 0.0020510039860339555
loss error: 0.0347
r

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0019530664749425961
loss error: 0.0532
round 98, starting client 2/49, id: 1
Epoch [1/1], Train Loss: 0.002068147998458395
loss error: 0.0403
round 98, starting client 3/49, id: 2
Epoch [1/1], Train Loss: 0.0022947321219059327
loss error: 0.0368
round 98, starting client 4/49, id: 3
Epoch [1/1], Train Loss: 0.002435798957651736
loss error: 0.0318
round 98, starting client 5/49, id: 4
Epoch [1/1], Train Loss: 0.0022160416648892524
loss error: 0.0362
round 98, starting client 6/49, id: 5
Epoch [1/1], Train Loss: 0.0021812138322275135
loss error: 0.0320
round 98, starting client 7/49, id: 6
Epoch [1/1], Train Loss: 0.002066384341781707
loss error: 0.0416
round 98, starting client 8/49, id: 7
Epoch [1/1], Train Loss: 0.0015470136016308557
loss error: 0.0404
round 98, starting client 9/49, id: 8
Epoch [1/1], Train Loss: 0.002765176168535477
loss error: 0.0251
round 98, starting client 10/49, id: 9
Epoch [1/1], Train Loss: 0.0020431105259814536
loss error: 0.0269
r

In [21]:
loss_csakd = np.insert(loss_csakd, 0, loss_csakd1)
smape_csakd = np.insert(smape_csakd, 0, smape_csakd1)
mae_csakd = np.insert(mae_csakd, 0, mae_csakd1)
rmse_csakd = np.insert(mae_csakd, 0, mae_csakd1)

In [22]:
np.save(f'metrics/fedcsakd_outputs_C{n_clients}.npy', np.array(outputs_csakd, dtype=object))
np.save(f'metrics/fedcsakd_targets_C{n_clients}.npy', np.array(targets_csakd, dtype=object))
np.save(f'metrics/fedcsakd_loss_C{n_clients}.npy', loss_csakd)
np.save(f'metrics/fedcsakd_smape_C{n_clients}.npy', smape_csakd)
np.save(f'metrics/fedcsakd_mae_C{n_clients}.npy', mae_csakd)
np.save(f'metrics/fedcsakd_rmse_C{n_clients}.npy', rmse_csakd)

## 70

In [8]:
n_clients=70

In [9]:
train_loader = []
test_loader = []
label_scalers = []
i=0
for _, df in dataframes.items():
    if i==n_clients:
        break
    inputs_cols_indices = range(0, df.shape[1])  # use (total_demand,Year,Month,Day,Hour,Minute) columns as features
    #move the window
    inputs, labels = move_sliding_window(
        df.values,
        window_size,
        inputs_cols_indices=inputs_cols_indices,
        label_col_index=label_col_index
    )

    # Normalize the input data columns
    sc = MinMaxScaler()
    # Obtaining the scaler for the labels(usage data) so that output can be re-scaled to actual value during evaluation
    label_sc = MinMaxScaler()

    # Split data into train/test portions and combining all data into a single array
    test_portion = int(0.2 * len(inputs))

    train_x = sc.fit_transform(inputs[:-test_portion].reshape(-1, window_size * df.shape[1]))
    train_x = train_x.reshape(-1, window_size, df.shape[1])
    train_y = label_sc.fit_transform(labels[:-test_portion])

    test_x = sc.transform(inputs[-test_portion:].reshape(-1, window_size * df.shape[1]))
    test_x = test_x.reshape(-1, window_size, df.shape[1])
    test_y = label_sc.transform(labels[-test_portion:])

    # test_x.append(testx)
    # test_y.append(testy)
    label_scalers.append(label_sc)

    # pytorch data loaders
    train_data = TensorDataset(torch.from_numpy(train_x).to('cpu'), torch.from_numpy(train_y).to('cpu'))
    train_loader.append(DataLoader(train_data, batch_size=batch_size, drop_last=True))# Drop the last incomplete batch
    test_data = TensorDataset(torch.from_numpy(test_x).to('cpu'), torch.from_numpy(test_y).to('cpu'))
    test_loader.append(DataLoader(test_data, batch_size=batch_size))# Drop the last incomplete batch

    # release some memory
    del train_x, train_y
    i=i+1

(68093, 90, 9) (68093, 1)
(58528, 90, 9) (58528, 1)
(46750, 90, 9) (46750, 1)
(65300, 90, 9) (65300, 1)
(57086, 90, 9) (57086, 1)
(51617, 90, 9) (51617, 1)
(47363, 90, 9) (47363, 1)
(68901, 90, 9) (68901, 1)
(67168, 90, 9) (67168, 1)
(69578, 90, 9) (69578, 1)
(62003, 90, 9) (62003, 1)
(49050, 90, 9) (49050, 1)
(61853, 90, 9) (61853, 1)
(69521, 90, 9) (69521, 1)
(67302, 90, 9) (67302, 1)
(72217, 90, 9) (72217, 1)
(46055, 90, 9) (46055, 1)
(57157, 90, 9) (57157, 1)
(64807, 90, 9) (64807, 1)
(66845, 90, 9) (66845, 1)
(61800, 90, 9) (61800, 1)
(55024, 90, 9) (55024, 1)
(65910, 90, 9) (65910, 1)
(49996, 90, 9) (49996, 1)
(63049, 90, 9) (63049, 1)
(64836, 90, 9) (64836, 1)
(64007, 90, 9) (64007, 1)
(69858, 90, 9) (69858, 1)
(56491, 90, 9) (56491, 1)
(65359, 90, 9) (65359, 1)
(61733, 90, 9) (61733, 1)
(66320, 90, 9) (66320, 1)
(61236, 90, 9) (61236, 1)
(71305, 90, 9) (71305, 1)
(52888, 90, 9) (52888, 1)
(58160, 90, 9) (58160, 1)
(70972, 90, 9) (70972, 1)
(61987, 90, 9) (61987, 1)
(43972, 90, 

In [10]:
%%time
lstm_csakd = copy.deepcopy(lstm)
outputs_csakd1, targets_csakd1, loss_csakd1, smape_csakd1, mae_csakd1, rmse_csakd1,global_model, aggregated_logits = fedavg(
    global_model = lstm_csakd,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = 1,
    model_type = model_type,
    device = device,
)
outputs_csakd, targets_csakd, loss_csakd, smape_csakd, mae_csakd, rmse_csakd = fedcsakd(
    global_model = global_model,
    aggregated_logits=aggregated_logits,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds-1,
    model_type = model_type,
    device = device,
)


starting avg round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69]
round 0, starting client 1/70, id: 0
Epoch [1/1], Train Loss: 0.09309540379722162
round 0, starting client 2/70, id: 1
Epoch [1/1], Train Loss: 0.0819098582284318
round 0, starting client 3/70, id: 2
Epoch [1/1], Train Loss: 0.07043305091145964
round 0, starting client 4/70, id: 3
Epoch [1/1], Train Loss: 0.07208150037217373
round 0, starting client 5/70, id: 4
Epoch [1/1], Train Loss: 0.08735707834024321
round 0, starting client 6/70, id: 5
Epoch [1/1], Train Loss: 0.07800133721902965
round 0, starting client 7/70, id: 6
Epoch [1/1], Train Loss: 0.09574713729120592
round 0, starting client 8/70, id: 7
Epoch [1/1], Train Loss: 0.07787519658230385
round 0, starting client 9/70, id: 8
Epoch [1/1], Train Loss: 0.07854818477510259
round 0, starting

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.059115847642972785
loss error: 0.0316
round 1, starting client 2/70, id: 1
Epoch [1/1], Train Loss: 0.04901238501899771
loss error: 0.0478
round 1, starting client 3/70, id: 2
Epoch [1/1], Train Loss: 0.04285831766254786
loss error: 0.0447
round 1, starting client 4/70, id: 3
Epoch [1/1], Train Loss: 0.047445458049575485
loss error: 0.0326
round 1, starting client 5/70, id: 4
Epoch [1/1], Train Loss: 0.05291246229105376
loss error: 0.0355
round 1, starting client 6/70, id: 5
Epoch [1/1], Train Loss: 0.04794955437537284
loss error: 0.0503
round 1, starting client 7/70, id: 6
Epoch [1/1], Train Loss: 0.058064934923439435
loss error: 0.0499
round 1, starting client 8/70, id: 7
Epoch [1/1], Train Loss: 0.04580278111235152
loss error: 0.0386
round 1, starting client 9/70, id: 8
Epoch [1/1], Train Loss: 0.05131526893148056
loss error: 0.0498
round 1, starting client 10/70, id: 9
Epoch [1/1], Train Loss: 0.042222661000710954
loss error: 0.0503
round 1, starting clie

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.04422208368075344
loss error: 0.0394
round 2, starting client 2/70, id: 1
Epoch [1/1], Train Loss: 0.03701968836701579
loss error: 0.0228
round 2, starting client 3/70, id: 2
Epoch [1/1], Train Loss: 0.03556162051649557
loss error: 0.0392
round 2, starting client 4/70, id: 3
Epoch [1/1], Train Loss: 0.03839451164080232
loss error: 0.0195
round 2, starting client 5/70, id: 4
Epoch [1/1], Train Loss: 0.039725606964731756
loss error: 0.0885
round 2, starting client 6/70, id: 5
Epoch [1/1], Train Loss: 0.037306578038260346
loss error: 0.0281
round 2, starting client 7/70, id: 6
Epoch [1/1], Train Loss: 0.04266446808705459
loss error: 0.0296
round 2, starting client 8/70, id: 7
Epoch [1/1], Train Loss: 0.034190723215633975
loss error: 0.0235
round 2, starting client 9/70, id: 8
Epoch [1/1], Train Loss: 0.04046397391133584
loss error: 0.0605
round 2, starting client 10/70, id: 9
Epoch [1/1], Train Loss: 0.0315427689778584
loss error: 0.0421
round 2, starting client

...

Epoch [1/1], Train Loss: 0.002022104361424012
loss error: 0.0261
round 96, starting client 2/64, id: 1
Epoch [1/1], Train Loss: 0.002153408910251326
loss error: 0.0230
round 96, starting client 3/64, id: 2
Epoch [1/1], Train Loss: 0.0023211293486787733
loss error: 0.0794
round 96, starting client 4/64, id: 3
Epoch [1/1], Train Loss: 0.0025689433358481854
loss error: 0.0654
round 96, starting client 5/64, id: 4
Epoch [1/1], Train Loss: 0.002318195674557832
loss error: 0.0444
round 96, starting client 6/64, id: 5
Epoch [1/1], Train Loss: 0.0022621492666075943
loss error: 0.0382
round 96, starting client 7/64, id: 6
Epoch [1/1], Train Loss: 0.0021544808893137284
loss error: 0.0315
round 96, starting client 8/64, id: 7
Epoch [1/1], Train Loss: 0.0015750168778775433
loss error: 0.0655
round 96, starting client 9/64, id: 8
Epoch [1/1], Train Loss: 0.002878420719823156
loss error: 0.0350
round 96, starting client 10/64, id: 9
Epoch [1/1], Train Loss: 0.002115057447992041
loss error: 0.0635
ro

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.002019065798519461
loss error: 0.0482
round 97, starting client 2/64, id: 1
Epoch [1/1], Train Loss: 0.002149442084030144
loss error: 0.0346
round 97, starting client 3/64, id: 2
Epoch [1/1], Train Loss: 0.002316943372231132
loss error: 0.0416
round 97, starting client 4/64, id: 3
Epoch [1/1], Train Loss: 0.0025642700493335724
loss error: 0.0852
round 97, starting client 5/64, id: 4
Epoch [1/1], Train Loss: 0.0023140833906257867
loss error: 0.0413
round 97, starting client 6/64, id: 5
Epoch [1/1], Train Loss: 0.0022579279786441478
loss error: 0.0624
round 97, starting client 7/64, id: 6
Epoch [1/1], Train Loss: 0.0021496247641767403
loss error: 0.0450
round 97, starting client 8/64, id: 7
Epoch [1/1], Train Loss: 0.0015726230125918212
loss error: 0.0343
round 97, starting client 9/64, id: 8
Epoch [1/1], Train Loss: 0.0028736105752893933
loss error: 0.0580
round 97, starting client 10/64, id: 9
Epoch [1/1], Train Loss: 0.00211109229847487
loss error: 0.0252
ro

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0020153280545272072
loss error: 0.0257
round 98, starting client 2/64, id: 1
Epoch [1/1], Train Loss: 0.002145741850189451
loss error: 0.0519
round 98, starting client 3/64, id: 2
Epoch [1/1], Train Loss: 0.00231252153672459
loss error: 0.0365
round 98, starting client 4/64, id: 3
Epoch [1/1], Train Loss: 0.0025598939391784366
loss error: 0.0406
round 98, starting client 5/64, id: 4
Epoch [1/1], Train Loss: 0.002309892913961614
loss error: 0.0472
round 98, starting client 6/64, id: 5
Epoch [1/1], Train Loss: 0.0022534344840096305
loss error: 0.0354
round 98, starting client 7/64, id: 6
Epoch [1/1], Train Loss: 0.002139923787310821
loss error: 0.0224
round 98, starting client 8/64, id: 7
Epoch [1/1], Train Loss: 0.0015701322590071214
loss error: 0.0638
round 98, starting client 9/64, id: 8
Epoch [1/1], Train Loss: 0.0028684046813465956
loss error: 0.0321
round 98, starting client 10/64, id: 9
Epoch [1/1], Train Loss: 0.0021077143044547276
loss error: 0.0454
ro

In [11]:
loss_csakd = np.insert(loss_csakd, 0, loss_csakd1)
smape_csakd = np.insert(smape_csakd, 0, smape_csakd1)
mae_csakd = np.insert(mae_csakd, 0, mae_csakd1)
rmse_csakd = np.insert(mae_csakd, 0, mae_csakd1)

In [12]:
np.save(f'metrics/fedcsakd_outputs_C{n_clients}.npy', np.array(outputs_csakd, dtype=object))
np.save(f'metrics/fedcsakd_targets_C{n_clients}.npy', np.array(targets_csakd, dtype=object))
np.save(f'metrics/fedcsakd_loss_C{n_clients}.npy', loss_csakd)
np.save(f'metrics/fedcsakd_smape_C{n_clients}.npy', smape_csakd)
np.save(f'metrics/fedcsakd_mae_C{n_clients}.npy', mae_csakd)
np.save(f'metrics/fedcsakd_rmse_C{n_clients}.npy', rmse_csakd)

## 80

In [13]:
n_clients=80

In [14]:
train_loader = []
test_loader = []
label_scalers = []
i=0
for _, df in dataframes.items():
    if i==n_clients:
        break
    inputs_cols_indices = range(0, df.shape[1])  # use (total_demand,Year,Month,Day,Hour,Minute) columns as features
    #move the window
    inputs, labels = move_sliding_window(
        df.values,
        window_size,
        inputs_cols_indices=inputs_cols_indices,
        label_col_index=label_col_index
    )

    # Normalize the input data columns
    sc = MinMaxScaler()
    # Obtaining the scaler for the labels(usage data) so that output can be re-scaled to actual value during evaluation
    label_sc = MinMaxScaler()

    # Split data into train/test portions and combining all data into a single array
    test_portion = int(0.2 * len(inputs))

    train_x = sc.fit_transform(inputs[:-test_portion].reshape(-1, window_size * df.shape[1]))
    train_x = train_x.reshape(-1, window_size, df.shape[1])
    train_y = label_sc.fit_transform(labels[:-test_portion])

    test_x = sc.transform(inputs[-test_portion:].reshape(-1, window_size * df.shape[1]))
    test_x = test_x.reshape(-1, window_size, df.shape[1])
    test_y = label_sc.transform(labels[-test_portion:])

    # test_x.append(testx)
    # test_y.append(testy)
    label_scalers.append(label_sc)

    # pytorch data loaders
    train_data = TensorDataset(torch.from_numpy(train_x).to('cpu'), torch.from_numpy(train_y).to('cpu'))
    train_loader.append(DataLoader(train_data, batch_size=batch_size, drop_last=True))# Drop the last incomplete batch
    test_data = TensorDataset(torch.from_numpy(test_x).to('cpu'), torch.from_numpy(test_y).to('cpu'))
    test_loader.append(DataLoader(test_data, batch_size=batch_size))# Drop the last incomplete batch

    # release some memory
    del train_x, train_y
    i=i+1

(68093, 90, 9) (68093, 1)
(58528, 90, 9) (58528, 1)
(46750, 90, 9) (46750, 1)
(65300, 90, 9) (65300, 1)
(57086, 90, 9) (57086, 1)
(51617, 90, 9) (51617, 1)
(47363, 90, 9) (47363, 1)
(68901, 90, 9) (68901, 1)
(67168, 90, 9) (67168, 1)
(69578, 90, 9) (69578, 1)
(62003, 90, 9) (62003, 1)
(49050, 90, 9) (49050, 1)
(61853, 90, 9) (61853, 1)
(69521, 90, 9) (69521, 1)
(67302, 90, 9) (67302, 1)
(72217, 90, 9) (72217, 1)
(46055, 90, 9) (46055, 1)
(57157, 90, 9) (57157, 1)
(64807, 90, 9) (64807, 1)
(66845, 90, 9) (66845, 1)
(61800, 90, 9) (61800, 1)
(55024, 90, 9) (55024, 1)
(65910, 90, 9) (65910, 1)
(49996, 90, 9) (49996, 1)
(63049, 90, 9) (63049, 1)
(64836, 90, 9) (64836, 1)
(64007, 90, 9) (64007, 1)
(69858, 90, 9) (69858, 1)
(56491, 90, 9) (56491, 1)
(65359, 90, 9) (65359, 1)
(61733, 90, 9) (61733, 1)
(66320, 90, 9) (66320, 1)
(61236, 90, 9) (61236, 1)
(71305, 90, 9) (71305, 1)
(52888, 90, 9) (52888, 1)
(58160, 90, 9) (58160, 1)
(70972, 90, 9) (70972, 1)
(61987, 90, 9) (61987, 1)
(43972, 90, 

In [15]:
%%time
lstm_csakd = copy.deepcopy(lstm)
outputs_csakd1, targets_csakd1, loss_csakd1, smape_csakd1, mae_csakd1, rmse_csakd1,global_model, aggregated_logits = fedavg(
    global_model = lstm_csakd,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = 1,
    model_type = model_type,
    device = device,
)
outputs_csakd, targets_csakd, loss_csakd, smape_csakd, mae_csakd, rmse_csakd = fedcsakd(
    global_model = global_model,
    aggregated_logits=aggregated_logits,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds-1,
    model_type = model_type,
    device = device,
)


starting avg round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69 70 71
 72 73 74 75 76 77 78 79]
round 0, starting client 1/80, id: 0
Epoch [1/1], Train Loss: 0.09309540379722162
round 0, starting client 2/80, id: 1
Epoch [1/1], Train Loss: 0.0819098582284318
round 0, starting client 3/80, id: 2
Epoch [1/1], Train Loss: 0.07043305091145964
round 0, starting client 4/80, id: 3
Epoch [1/1], Train Loss: 0.07208150037217373
round 0, starting client 5/80, id: 4
Epoch [1/1], Train Loss: 0.08735707834024321
round 0, starting client 6/80, id: 5
Epoch [1/1], Train Loss: 0.07800133721902965
round 0, starting client 7/80, id: 6
Epoch [1/1], Train Loss: 0.09574713729120592
round 0, starting client 8/80, id: 7
Epoch [1/1], Train Loss: 0.07787519658230385
round 0, starting client 9/80, id: 8
Epoch [1/1], Train Loss: 0.0785

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.05920805138939956
loss error: 0.0259
round 1, starting client 2/80, id: 1
Epoch [1/1], Train Loss: 0.04909319310552544
loss error: 0.0749
round 1, starting client 3/80, id: 2
Epoch [1/1], Train Loss: 0.04291734559875395
loss error: 0.0262
round 1, starting client 4/80, id: 3
Epoch [1/1], Train Loss: 0.04750163182981458
loss error: 0.0716
round 1, starting client 5/80, id: 4
Epoch [1/1], Train Loss: 0.05300027690827847
loss error: 0.0282
round 1, starting client 6/80, id: 5
Epoch [1/1], Train Loss: 0.04802360595203936
loss error: 0.0632
round 1, starting client 7/80, id: 6
Epoch [1/1], Train Loss: 0.05817607961393691
loss error: 0.0538
round 1, starting client 8/80, id: 7
Epoch [1/1], Train Loss: 0.04587870888974307
loss error: 0.0511
round 1, starting client 9/80, id: 8
Epoch [1/1], Train Loss: 0.05137972408332506
loss error: 0.0610
round 1, starting client 10/80, id: 9
Epoch [1/1], Train Loss: 0.042280598164156635
loss error: 0.0337
round 1, starting client 

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.04432082538194249
loss error: 0.0478
round 2, starting client 2/80, id: 1
Epoch [1/1], Train Loss: 0.03713102624234227
loss error: 0.0439
round 2, starting client 3/80, id: 2
Epoch [1/1], Train Loss: 0.03569015027541254
loss error: 0.0297
round 2, starting client 4/80, id: 3
Epoch [1/1], Train Loss: 0.03852210997366438
loss error: 0.0298
round 2, starting client 5/80, id: 4
Epoch [1/1], Train Loss: 0.0398284265009517
loss error: 0.0421
round 2, starting client 6/80, id: 5
Epoch [1/1], Train Loss: 0.03741638003848494
loss error: 0.0769
round 2, starting client 7/80, id: 6
Epoch [1/1], Train Loss: 0.042768300636797325
loss error: 0.0415
round 2, starting client 8/80, id: 7
Epoch [1/1], Train Loss: 0.03428112870117404
loss error: 0.0404
round 2, starting client 9/80, id: 8
Epoch [1/1], Train Loss: 0.04057154385372996
loss error: 0.0306
round 2, starting client 10/80, id: 9
Epoch [1/1], Train Loss: 0.03163342157171832
loss error: 0.0395
round 2, starting client 1

...

Epoch [1/1], Train Loss: 0.0020310685482262726
loss error: 0.0546
round 96, starting client 2/73, id: 1
Epoch [1/1], Train Loss: 0.0021720900756513908
loss error: 0.0660
round 96, starting client 3/73, id: 2
Epoch [1/1], Train Loss: 0.002312103158652058
loss error: 0.0321
round 96, starting client 4/73, id: 3
Epoch [1/1], Train Loss: 0.0025847913804646653
loss error: 0.0421
round 96, starting client 5/73, id: 4
Epoch [1/1], Train Loss: 0.002336516140282832
loss error: 0.0411
round 96, starting client 6/73, id: 5
Epoch [1/1], Train Loss: 0.0022787856229115277
loss error: 0.0411
round 96, starting client 7/73, id: 6
Epoch [1/1], Train Loss: 0.0021752055775298663
loss error: 0.0375
round 96, starting client 8/73, id: 7
Epoch [1/1], Train Loss: 0.0015812110955352489
loss error: 0.0375
round 96, starting client 9/73, id: 8
Epoch [1/1], Train Loss: 0.0029066314835710302
loss error: 0.0333
round 96, starting client 10/73, id: 9
Epoch [1/1], Train Loss: 0.0021282593839310328
loss error: 0.0515

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0020287905974568413
loss error: 0.0296
round 97, starting client 2/73, id: 1
Epoch [1/1], Train Loss: 0.0021692494124484563
loss error: 0.0585
round 97, starting client 3/73, id: 2
Epoch [1/1], Train Loss: 0.002308312843928838
loss error: 0.0525
round 97, starting client 4/73, id: 3
Epoch [1/1], Train Loss: 0.0025809880850526175
loss error: 0.0257
round 97, starting client 5/73, id: 4
Epoch [1/1], Train Loss: 0.0023333126128735867
loss error: 0.0433
round 97, starting client 6/73, id: 5
Epoch [1/1], Train Loss: 0.0022753805402317075
loss error: 0.0353
round 97, starting client 7/73, id: 6
Epoch [1/1], Train Loss: 0.002172137700285561
loss error: 0.0526
round 97, starting client 8/73, id: 7
Epoch [1/1], Train Loss: 0.0015796463462119958
loss error: 0.0502
round 97, starting client 9/73, id: 8
Epoch [1/1], Train Loss: 0.0029016306731276787
loss error: 0.0421
round 97, starting client 10/73, id: 9
Epoch [1/1], Train Loss: 0.0021254102525913544
loss error: 0.0308

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.002025979266827047
loss error: 0.0656
round 98, starting client 2/73, id: 1
Epoch [1/1], Train Loss: 0.0021663428594668713
loss error: 0.0229
round 98, starting client 3/73, id: 2
Epoch [1/1], Train Loss: 0.0023049435112625365
loss error: 0.0638
round 98, starting client 4/73, id: 3
Epoch [1/1], Train Loss: 0.0025770635328109504
loss error: 0.0462
round 98, starting client 5/73, id: 4
Epoch [1/1], Train Loss: 0.0023296761276221586
loss error: 0.0626
round 98, starting client 6/73, id: 5
Epoch [1/1], Train Loss: 0.0022716888444847434
loss error: 0.0445
round 98, starting client 7/73, id: 6
Epoch [1/1], Train Loss: 0.002168454212526715
loss error: 0.0321
round 98, starting client 8/73, id: 7
Epoch [1/1], Train Loss: 0.0015774853022347357
loss error: 0.0437
round 98, starting client 9/73, id: 8
Epoch [1/1], Train Loss: 0.002896933846596557
loss error: 0.0294
round 98, starting client 10/73, id: 9
Epoch [1/1], Train Loss: 0.0021224325254378426
loss error: 0.0280


In [16]:
loss_csakd = np.insert(loss_csakd, 0, loss_csakd1)
smape_csakd = np.insert(smape_csakd, 0, smape_csakd1)
mae_csakd = np.insert(mae_csakd, 0, mae_csakd1)
rmse_csakd = np.insert(mae_csakd, 0, mae_csakd1)

In [17]:
np.save(f'metrics/fedcsakd_outputs_C{n_clients}.npy', np.array(outputs_csakd, dtype=object))
np.save(f'metrics/fedcsakd_targets_C{n_clients}.npy', np.array(targets_csakd, dtype=object))
np.save(f'metrics/fedcsakd_loss_C{n_clients}.npy', loss_csakd)
np.save(f'metrics/fedcsakd_smape_C{n_clients}.npy', smape_csakd)
np.save(f'metrics/fedcsakd_mae_C{n_clients}.npy', mae_csakd)
np.save(f'metrics/fedcsakd_rmse_C{n_clients}.npy', rmse_csakd)

## 90

In [18]:
n_clients=90

In [19]:
train_loader = []
test_loader = []
label_scalers = []
i=0
for _, df in dataframes.items():
    if i==n_clients:
        break
    inputs_cols_indices = range(0, df.shape[1])  # use (total_demand,Year,Month,Day,Hour,Minute) columns as features
    #move the window
    inputs, labels = move_sliding_window(
        df.values,
        window_size,
        inputs_cols_indices=inputs_cols_indices,
        label_col_index=label_col_index
    )

    # Normalize the input data columns
    sc = MinMaxScaler()
    # Obtaining the scaler for the labels(usage data) so that output can be re-scaled to actual value during evaluation
    label_sc = MinMaxScaler()

    # Split data into train/test portions and combining all data into a single array
    test_portion = int(0.2 * len(inputs))

    train_x = sc.fit_transform(inputs[:-test_portion].reshape(-1, window_size * df.shape[1]))
    train_x = train_x.reshape(-1, window_size, df.shape[1])
    train_y = label_sc.fit_transform(labels[:-test_portion])

    test_x = sc.transform(inputs[-test_portion:].reshape(-1, window_size * df.shape[1]))
    test_x = test_x.reshape(-1, window_size, df.shape[1])
    test_y = label_sc.transform(labels[-test_portion:])

    # test_x.append(testx)
    # test_y.append(testy)
    label_scalers.append(label_sc)

    # pytorch data loaders
    train_data = TensorDataset(torch.from_numpy(train_x).to('cpu'), torch.from_numpy(train_y).to('cpu'))
    train_loader.append(DataLoader(train_data, batch_size=batch_size, drop_last=True))# Drop the last incomplete batch
    test_data = TensorDataset(torch.from_numpy(test_x).to('cpu'), torch.from_numpy(test_y).to('cpu'))
    test_loader.append(DataLoader(test_data, batch_size=batch_size))# Drop the last incomplete batch

    # release some memory
    del train_x, train_y
    i=i+1

(68093, 90, 9) (68093, 1)
(58528, 90, 9) (58528, 1)
(46750, 90, 9) (46750, 1)
(65300, 90, 9) (65300, 1)
(57086, 90, 9) (57086, 1)
(51617, 90, 9) (51617, 1)
(47363, 90, 9) (47363, 1)
(68901, 90, 9) (68901, 1)
(67168, 90, 9) (67168, 1)
(69578, 90, 9) (69578, 1)
(62003, 90, 9) (62003, 1)
(49050, 90, 9) (49050, 1)
(61853, 90, 9) (61853, 1)
(69521, 90, 9) (69521, 1)
(67302, 90, 9) (67302, 1)
(72217, 90, 9) (72217, 1)
(46055, 90, 9) (46055, 1)
(57157, 90, 9) (57157, 1)
(64807, 90, 9) (64807, 1)
(66845, 90, 9) (66845, 1)
(61800, 90, 9) (61800, 1)
(55024, 90, 9) (55024, 1)
(65910, 90, 9) (65910, 1)
(49996, 90, 9) (49996, 1)
(63049, 90, 9) (63049, 1)
(64836, 90, 9) (64836, 1)
(64007, 90, 9) (64007, 1)
(69858, 90, 9) (69858, 1)
(56491, 90, 9) (56491, 1)
(65359, 90, 9) (65359, 1)
(61733, 90, 9) (61733, 1)
(66320, 90, 9) (66320, 1)
(61236, 90, 9) (61236, 1)
(71305, 90, 9) (71305, 1)
(52888, 90, 9) (52888, 1)
(58160, 90, 9) (58160, 1)
(70972, 90, 9) (70972, 1)
(61987, 90, 9) (61987, 1)
(43972, 90, 

In [20]:
%%time
lstm_csakd = copy.deepcopy(lstm)
outputs_csakd1, targets_csakd1, loss_csakd1, smape_csakd1, mae_csakd1, rmse_csakd1,global_model, aggregated_logits = fedavg(
    global_model = lstm_csakd,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = 1,
    model_type = model_type,
    device = device,
)
outputs_csakd, targets_csakd, loss_csakd, smape_csakd, mae_csakd, rmse_csakd = fedcsakd(
    global_model = global_model,
    aggregated_logits=aggregated_logits,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds-1,
    model_type = model_type,
    device = device,
)


starting avg round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69 70 71
 72 73 74 75 76 77 78 79 80 81 82 83 84 85 86 87 88 89]
round 0, starting client 1/90, id: 0
Epoch [1/1], Train Loss: 0.09309540379722162
round 0, starting client 2/90, id: 1
Epoch [1/1], Train Loss: 0.0819098582284318
round 0, starting client 3/90, id: 2
Epoch [1/1], Train Loss: 0.07043305091145964
round 0, starting client 4/90, id: 3
Epoch [1/1], Train Loss: 0.07208150037217373
round 0, starting client 5/90, id: 4
Epoch [1/1], Train Loss: 0.08735707834024321
round 0, starting client 6/90, id: 5
Epoch [1/1], Train Loss: 0.07800133721902965
round 0, starting client 7/90, id: 6
Epoch [1/1], Train Loss: 0.09574713729120592
round 0, starting client 8/90, id: 7
Epoch [1/1], Train Loss: 0.07787519658230385
round 0, starting client 9/90, id: 8
E

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.05906035937368869
loss error: 0.0330
round 1, starting client 2/90, id: 1
Epoch [1/1], Train Loss: 0.048961067116922816
loss error: 0.0324
round 1, starting client 3/90, id: 2
Epoch [1/1], Train Loss: 0.042817073369709156
loss error: 0.0674
round 1, starting client 4/90, id: 3
Epoch [1/1], Train Loss: 0.04740677684472471
loss error: 0.0304
round 1, starting client 5/90, id: 4
Epoch [1/1], Train Loss: 0.05285819399763237
loss error: 0.0301
round 1, starting client 6/90, id: 5
Epoch [1/1], Train Loss: 0.04790320703759788
loss error: 0.0527
round 1, starting client 7/90, id: 6
Epoch [1/1], Train Loss: 0.05800735009079046
loss error: 0.0449
round 1, starting client 8/90, id: 7
Epoch [1/1], Train Loss: 0.04574983950071738
loss error: 0.0258
round 1, starting client 9/90, id: 8
Epoch [1/1], Train Loss: 0.05127256653773098
loss error: 0.0549
round 1, starting client 10/90, id: 9
Epoch [1/1], Train Loss: 0.04217709618172161
loss error: 0.0275
round 1, starting client

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.04413796648523717
loss error: 0.0257
round 2, starting client 2/90, id: 1
Epoch [1/1], Train Loss: 0.03702124297204945
loss error: 0.0320
round 2, starting client 3/90, id: 2
Epoch [1/1], Train Loss: 0.035664668565409056
loss error: 0.0388
round 2, starting client 4/90, id: 3
Epoch [1/1], Train Loss: 0.038448387720421244
loss error: 0.0382
round 2, starting client 5/90, id: 4
Epoch [1/1], Train Loss: 0.03968701113692738
loss error: 0.0524
round 2, starting client 6/90, id: 5
Epoch [1/1], Train Loss: 0.03731779088266194
loss error: 0.0308
round 2, starting client 7/90, id: 6
Epoch [1/1], Train Loss: 0.04260986746364348
loss error: 0.0443
round 2, starting client 8/90, id: 7
Epoch [1/1], Train Loss: 0.034154468057852876
loss error: 0.0365
round 2, starting client 9/90, id: 8
Epoch [1/1], Train Loss: 0.04045774755426324
loss error: 0.0308
round 2, starting client 10/90, id: 9
Epoch [1/1], Train Loss: 0.031515890318486416
loss error: 0.0394
round 2, starting clie

...

Epoch [1/1], Train Loss: 0.0020331463409710747
loss error: 0.0453
round 96, starting client 2/81, id: 1
Epoch [1/1], Train Loss: 0.0021730244159698484
loss error: 0.0298
round 96, starting client 3/81, id: 2
Epoch [1/1], Train Loss: 0.0023325422371271993
loss error: 0.0718
round 96, starting client 4/81, id: 3
Epoch [1/1], Train Loss: 0.002589266556634695
loss error: 0.0393
round 96, starting client 5/81, id: 4
Epoch [1/1], Train Loss: 0.0023352815505032513
loss error: 0.0320
round 96, starting client 6/81, id: 5
Epoch [1/1], Train Loss: 0.002287981586414389
loss error: 0.0420
round 96, starting client 7/81, id: 6
Epoch [1/1], Train Loss: 0.0021889450711298835
loss error: 0.0583
round 96, starting client 8/81, id: 7
Epoch [1/1], Train Loss: 0.0015833612865293922
loss error: 0.0455
round 96, starting client 9/81, id: 8
Epoch [1/1], Train Loss: 0.0029188645074520124
loss error: 0.0267
round 96, starting client 10/81, id: 9
Epoch [1/1], Train Loss: 0.002132376881760407
loss error: 0.0513


C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0020310365208336765
loss error: 0.0465
round 97, starting client 2/81, id: 1
Epoch [1/1], Train Loss: 0.002169177167686737
loss error: 0.0389
round 97, starting client 3/81, id: 2
Epoch [1/1], Train Loss: 0.002330102931106618
loss error: 0.0596
round 97, starting client 4/81, id: 3
Epoch [1/1], Train Loss: 0.002585668356486541
loss error: 0.0416
round 97, starting client 5/81, id: 4
Epoch [1/1], Train Loss: 0.0023316659975204275
loss error: 0.0352
round 97, starting client 6/81, id: 5
Epoch [1/1], Train Loss: 0.0022845672123366968
loss error: 0.0406
round 97, starting client 7/81, id: 6
Epoch [1/1], Train Loss: 0.002184763011157613
loss error: 0.0309
round 97, starting client 8/81, id: 7
Epoch [1/1], Train Loss: 0.0015814216644942478
loss error: 0.0500
round 97, starting client 9/81, id: 8
Epoch [1/1], Train Loss: 0.0029138362912747733
loss error: 0.0332
round 97, starting client 10/81, id: 9
Epoch [1/1], Train Loss: 0.0021294440712490885
loss error: 0.0407
r

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0020285541387187003
loss error: 0.0380
round 98, starting client 2/81, id: 1
Epoch [1/1], Train Loss: 0.0021664491376011735
loss error: 0.0237
round 98, starting client 3/81, id: 2
Epoch [1/1], Train Loss: 0.0023252536670447118
loss error: 0.0325
round 98, starting client 4/81, id: 3
Epoch [1/1], Train Loss: 0.002582217791510345
loss error: 0.0445
round 98, starting client 5/81, id: 4
Epoch [1/1], Train Loss: 0.0023288027362220664
loss error: 0.0437
round 98, starting client 6/81, id: 5
Epoch [1/1], Train Loss: 0.0022807225861470218
loss error: 0.0514
round 98, starting client 7/81, id: 6
Epoch [1/1], Train Loss: 0.0021815589043890707
loss error: 0.0597
round 98, starting client 8/81, id: 7
Epoch [1/1], Train Loss: 0.0015794695409911002
loss error: 0.0561
round 98, starting client 9/81, id: 8
Epoch [1/1], Train Loss: 0.002909302058889387
loss error: 0.0378
round 98, starting client 10/81, id: 9
Epoch [1/1], Train Loss: 0.002126363411392688
loss error: 0.0436


In [21]:
loss_csakd = np.insert(loss_csakd, 0, loss_csakd1)
smape_csakd = np.insert(smape_csakd, 0, smape_csakd1)
mae_csakd = np.insert(mae_csakd, 0, mae_csakd1)
rmse_csakd = np.insert(mae_csakd, 0, mae_csakd1)

In [22]:
np.save(f'metrics/fedcsakd_outputs_C{n_clients}.npy', np.array(outputs_csakd, dtype=object))
np.save(f'metrics/fedcsakd_targets_C{n_clients}.npy', np.array(targets_csakd, dtype=object))
np.save(f'metrics/fedcsakd_loss_C{n_clients}.npy', loss_csakd)
np.save(f'metrics/fedcsakd_smape_C{n_clients}.npy', smape_csakd)
np.save(f'metrics/fedcsakd_mae_C{n_clients}.npy', mae_csakd)
np.save(f'metrics/fedcsakd_rmse_C{n_clients}.npy', rmse_csakd)